In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
import sklearn.metrics as mt
from sklearn.model_selection import GridSearchCV
from lightgbm import LGBMClassifier

In [3]:
weather_df=pd.read_csv("./data/pre_labeled_weather.csv", index_col = 0)


In [4]:
weather_df

location  MinTemp  MaxTemp  Rainfall  WindGustSpeed  WindGustDir  \
0             45     12.6     23.2       0.5            6.4            7   
1             45     10.6     24.1       1.8            6.5           15   
2             45     14.2     25.1       1.8            7.0            7   
3             45     12.1     21.1       1.8            6.1            7   
4             45     11.9     15.4       1.8            6.5            7   
...          ...      ...      ...       ...            ...          ...   
343701        17      9.8     20.3       1.8            4.8           14   
343702        17      7.9     21.5       1.8            5.4           14   
343703        17      8.3     19.9       1.8            3.6           11   
343704        17      8.2     22.7       1.8            4.1           11   
343705        17      9.5     23.7       1.8            3.9           11   

        Sunshine  Evaporation  TodayRain  TomorrowRain  ...  Temp9am  \
0          13.17          3.2          0             0  ...     18.3   
1          13.17          3.2          0             0  ...     18.6   
2          13.17          3.2          0             0  ...     22.2   
3          13.17          3.2          0             0  ...     17.0   
4          13.17          3.2          0             1  ...     14.7   
...          ...          ...        ...           ...  ...      ...   
343701     13.17          3.2          0             0  ...     14.4   
343702     13.17          3.2          0             0  ...     15.9   
343703     13.17          3.2          0             0  ...     13.0   
343704     13.17          3.2          0             0  ...     15.5   
343705     13.17          3.2          0             0  ...     17.3   

        Pressure3pm  WindDir3pm  Cloud3pm  Humidity3pm  WindSpeed3pm  Temp3pm  \
0             998.7           9       6.0         51.0           4.2     19.3   
1            1000.8           0       2.0         35.0           2.7     20.5   
2            1002.8           0       0.0         31.0           2.1     22.9   
3            1005.5           2       3.0         70.0           2.8     18.3   
4            1013.2           6       9.0         89.0           4.6     13.9   
...             ...         ...       ...          ...           ...      ...   
343701       1006.8           8       1.0         35.0           2.4     19.5   
343702       1006.5          15       7.0         42.0           2.2     20.6   
343703       1014.3           8       0.0         37.0           2.7     18.9   
343704       1014.0          11       0.0         39.0           2.6     21.3   
343705       1013.6          12       0.0         44.0           2.6     22.6   

        Year  Month  Day  
0       2012      5    5  
1       2012      5    6  
2       2012      5    7  
3       2012      5    8  
4       2012      5    9  
...      ...    ...  ...  
343701  2022      5    1  
343702  2022      5    2  
343703  2022      5    3  
343704  2022      5    4  
343705  2022      5    5  

[343706 rows x 25 columns]

In [5]:
Y = weather_df.TomorrowRain
X = weather_df.drop("TomorrowRain",axis=1)

In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size = 0.2,stratify = Y, random_state = 0)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=0)
e
print(X_train.shape ,X_val.shape, X_test.shape)

(219971, 24) (54993, 24) (68742, 24)


In [7]:
def get_clf_eval(y_test, pred=None):
    confusion = mt.confusion_matrix( y_test, pred)
    accuracy = mt.accuracy_score(y_test , pred)
    precision = mt.precision_score(y_test , pred)
    recall = mt.recall_score(y_test , pred)
    f1 = mt.f1_score(y_test,pred)

    print('오차 행렬:')
    print(confusion)
    
    print('\n정확도: {0:.4f} \n정밀도: {1:.4f} \n재현율: {2:.4f} \n    F1: {3:.4f}'.format(accuracy, precision, recall, f1))


In [19]:
lgbm_clf = LGBMClassifier(n_estimators=2000, num_leaves=95, subsample=0.8, min_child_samples=100,learning_rate = 0.12,
                          max_depth=128)

evals = [(X_train, y_train),(X_val, y_val)]
lgbm_clf.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="accuracy", eval_set=evals,
                verbose=True)

preds = lgbm_clf.predict(X_test)
get_clf_eval(y_test, preds)

C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	training's binary_logloss: 0.490627	valid_1's binary_logloss: 0.48965
[2]	training's binary_logloss: 0.478815	valid_1's binary_logloss: 0.478351
[3]	training's binary_logloss: 0.469607	valid_1's binary_logloss: 0.469528
[4]	training's binary_logloss: 0.461647	valid_1's binary_logloss: 0.462075
[5]	training's binary_logloss: 0.454989	valid_1's binary_logloss: 0.455756
[6]	training's binary_logloss: 0.449428	valid_1's binary_logloss: 0.450637
[7]	training's binary_logloss: 0.444729	valid_1's binary_logloss: 0.446227
[8]	training's binary_logloss: 0.440599	valid_1's binary_logloss: 0.442632
[9]	training's binary_logloss: 0.436873	valid_1's binary_logloss: 0.439294
[10]	training's binary_logloss: 0.433802	valid_1's binary_logloss: 0.4367
[11]	training's binary_logloss: 0.430839	valid_1's binary_logloss: 0.434054
[12]	training's binary_logloss: 0.427429	valid_1's binary_logloss: 0.431054
[13]	training's binary_logloss: 0.424976	valid_1's binary_logloss: 0.429022
[14]	training's binary_l

[111]	training's binary_logloss: 0.321757	valid_1's binary_logloss: 0.351061
[112]	training's binary_logloss: 0.321372	valid_1's binary_logloss: 0.350875
[113]	training's binary_logloss: 0.321073	valid_1's binary_logloss: 0.350854
[114]	training's binary_logloss: 0.320624	valid_1's binary_logloss: 0.350599
[115]	training's binary_logloss: 0.319732	valid_1's binary_logloss: 0.349832
[116]	training's binary_logloss: 0.319419	valid_1's binary_logloss: 0.349811
[117]	training's binary_logloss: 0.318246	valid_1's binary_logloss: 0.348746
[118]	training's binary_logloss: 0.317621	valid_1's binary_logloss: 0.348227
[119]	training's binary_logloss: 0.317049	valid_1's binary_logloss: 0.347987
[120]	training's binary_logloss: 0.316399	valid_1's binary_logloss: 0.347515
[121]	training's binary_logloss: 0.316134	valid_1's binary_logloss: 0.347467
[122]	training's binary_logloss: 0.315749	valid_1's binary_logloss: 0.347269
[123]	training's binary_logloss: 0.315484	valid_1's binary_logloss: 0.347247

[231]	training's binary_logloss: 0.274654	valid_1's binary_logloss: 0.327401
[232]	training's binary_logloss: 0.274461	valid_1's binary_logloss: 0.327421
[233]	training's binary_logloss: 0.273726	valid_1's binary_logloss: 0.32673
[234]	training's binary_logloss: 0.273375	valid_1's binary_logloss: 0.326603
[235]	training's binary_logloss: 0.273016	valid_1's binary_logloss: 0.326402
[236]	training's binary_logloss: 0.272641	valid_1's binary_logloss: 0.326161
[237]	training's binary_logloss: 0.272059	valid_1's binary_logloss: 0.325783
[238]	training's binary_logloss: 0.271804	valid_1's binary_logloss: 0.325781
[239]	training's binary_logloss: 0.271489	valid_1's binary_logloss: 0.325644
[240]	training's binary_logloss: 0.271299	valid_1's binary_logloss: 0.325661
[241]	training's binary_logloss: 0.270992	valid_1's binary_logloss: 0.32553
[242]	training's binary_logloss: 0.270728	valid_1's binary_logloss: 0.325504
[243]	training's binary_logloss: 0.270345	valid_1's binary_logloss: 0.325273
[

[345]	training's binary_logloss: 0.241776	valid_1's binary_logloss: 0.313412
[346]	training's binary_logloss: 0.241629	valid_1's binary_logloss: 0.313423
[347]	training's binary_logloss: 0.241446	valid_1's binary_logloss: 0.313401
[348]	training's binary_logloss: 0.241319	valid_1's binary_logloss: 0.313421
[349]	training's binary_logloss: 0.240787	valid_1's binary_logloss: 0.312966
[350]	training's binary_logloss: 0.240539	valid_1's binary_logloss: 0.312937
[351]	training's binary_logloss: 0.240293	valid_1's binary_logloss: 0.312861
[352]	training's binary_logloss: 0.240074	valid_1's binary_logloss: 0.312853
[353]	training's binary_logloss: 0.239741	valid_1's binary_logloss: 0.312686
[354]	training's binary_logloss: 0.239612	valid_1's binary_logloss: 0.312693
[355]	training's binary_logloss: 0.239219	valid_1's binary_logloss: 0.312349
[356]	training's binary_logloss: 0.239027	valid_1's binary_logloss: 0.312322
[357]	training's binary_logloss: 0.238637	valid_1's binary_logloss: 0.312011

...

[1016]	training's binary_logloss: 0.132648	valid_1's binary_logloss: 0.285223
[1017]	training's binary_logloss: 0.132549	valid_1's binary_logloss: 0.285226
[1018]	training's binary_logloss: 0.13244	valid_1's binary_logloss: 0.285224
[1019]	training's binary_logloss: 0.132323	valid_1's binary_logloss: 0.285166
[1020]	training's binary_logloss: 0.132206	valid_1's binary_logloss: 0.28517
[1021]	training's binary_logloss: 0.132075	valid_1's binary_logloss: 0.285138
[1022]	training's binary_logloss: 0.131972	valid_1's binary_logloss: 0.285142
[1023]	training's binary_logloss: 0.131859	valid_1's binary_logloss: 0.285175
[1024]	training's binary_logloss: 0.131796	valid_1's binary_logloss: 0.285198
[1025]	training's binary_logloss: 0.131686	valid_1's binary_logloss: 0.285156
[1026]	training's binary_logloss: 0.131565	valid_1's binary_logloss: 0.285138
[1027]	training's binary_logloss: 0.131464	valid_1's binary_logloss: 0.285167
[1028]	training's binary_logloss: 0.131368	valid_1's binary_loglos

[1130]	training's binary_logloss: 0.119486	valid_1's binary_logloss: 0.280869
[1131]	training's binary_logloss: 0.119416	valid_1's binary_logloss: 0.28084
[1132]	training's binary_logloss: 0.119347	valid_1's binary_logloss: 0.280872
[1133]	training's binary_logloss: 0.119254	valid_1's binary_logloss: 0.280851
[1134]	training's binary_logloss: 0.119174	valid_1's binary_logloss: 0.280879
[1135]	training's binary_logloss: 0.11907	valid_1's binary_logloss: 0.280867
[1136]	training's binary_logloss: 0.119004	valid_1's binary_logloss: 0.280896
[1137]	training's binary_logloss: 0.118903	valid_1's binary_logloss: 0.280857
[1138]	training's binary_logloss: 0.11881	valid_1's binary_logloss: 0.280867
[1139]	training's binary_logloss: 0.118731	valid_1's binary_logloss: 0.280851
[1140]	training's binary_logloss: 0.118628	valid_1's binary_logloss: 0.28082
[1141]	training's binary_logloss: 0.118575	valid_1's binary_logloss: 0.280831
[1142]	training's binary_logloss: 0.118461	valid_1's binary_logloss:

[1239]	training's binary_logloss: 0.109351	valid_1's binary_logloss: 0.279886
[1240]	training's binary_logloss: 0.109246	valid_1's binary_logloss: 0.279887
[1241]	training's binary_logloss: 0.10917	valid_1's binary_logloss: 0.279901
[1242]	training's binary_logloss: 0.109098	valid_1's binary_logloss: 0.279902
[1243]	training's binary_logloss: 0.109043	valid_1's binary_logloss: 0.279929
[1244]	training's binary_logloss: 0.108971	valid_1's binary_logloss: 0.279898
[1245]	training's binary_logloss: 0.108901	valid_1's binary_logloss: 0.279908
[1246]	training's binary_logloss: 0.108825	valid_1's binary_logloss: 0.279917
[1247]	training's binary_logloss: 0.108707	valid_1's binary_logloss: 0.279825
[1248]	training's binary_logloss: 0.108607	valid_1's binary_logloss: 0.27984
[1249]	training's binary_logloss: 0.108531	valid_1's binary_logloss: 0.279842
[1250]	training's binary_logloss: 0.108442	valid_1's binary_logloss: 0.279812
[1251]	training's binary_logloss: 0.108369	valid_1's binary_loglos

[1346]	training's binary_logloss: 0.100059	valid_1's binary_logloss: 0.278418
[1347]	training's binary_logloss: 0.0999785	valid_1's binary_logloss: 0.278402
[1348]	training's binary_logloss: 0.0998881	valid_1's binary_logloss: 0.278387
[1349]	training's binary_logloss: 0.0997883	valid_1's binary_logloss: 0.278342
[1350]	training's binary_logloss: 0.0996425	valid_1's binary_logloss: 0.278188
[1351]	training's binary_logloss: 0.0995901	valid_1's binary_logloss: 0.278184
[1352]	training's binary_logloss: 0.0995004	valid_1's binary_logloss: 0.278191
[1353]	training's binary_logloss: 0.0994013	valid_1's binary_logloss: 0.278195
[1354]	training's binary_logloss: 0.0992867	valid_1's binary_logloss: 0.278174
[1355]	training's binary_logloss: 0.0992061	valid_1's binary_logloss: 0.278126
[1356]	training's binary_logloss: 0.0991069	valid_1's binary_logloss: 0.278106
[1357]	training's binary_logloss: 0.0990325	valid_1's binary_logloss: 0.278119
[1358]	training's binary_logloss: 0.0989444	valid_1's

[1453]	training's binary_logloss: 0.0920384	valid_1's binary_logloss: 0.278328
[1454]	training's binary_logloss: 0.091984	valid_1's binary_logloss: 0.27838
[1455]	training's binary_logloss: 0.0919358	valid_1's binary_logloss: 0.278389
[1456]	training's binary_logloss: 0.0918505	valid_1's binary_logloss: 0.278374
[1457]	training's binary_logloss: 0.0917883	valid_1's binary_logloss: 0.278379
[1458]	training's binary_logloss: 0.0917229	valid_1's binary_logloss: 0.27842
[1459]	training's binary_logloss: 0.0916652	valid_1's binary_logloss: 0.278444
[1460]	training's binary_logloss: 0.0915902	valid_1's binary_logloss: 0.278442
[1461]	training's binary_logloss: 0.0915377	valid_1's binary_logloss: 0.278441
[1462]	training's binary_logloss: 0.0914699	valid_1's binary_logloss: 0.278444
[1463]	training's binary_logloss: 0.091411	valid_1's binary_logloss: 0.278478
[1464]	training's binary_logloss: 0.0913477	valid_1's binary_logloss: 0.278487
[1465]	training's binary_logloss: 0.0912852	valid_1's bi

In [21]:
lgbm_clf = LGBMClassifier(n_estimators=2000, num_leaves=100, subsample=0.6, min_child_samples=100,learning_rate = 0.12,
                          max_depth=128,col)

evals = [(X_train, y_train),(X_val, y_val)]
lgbm_clf.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="accuracy", eval_set=evals,
                verbose=True)

preds = lgbm_clf.predict(X_test)
get_clf_eval(y_test, preds)

C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	training's binary_logloss: 0.490507	valid_1's binary_logloss: 0.489537
[2]	training's binary_logloss: 0.478591	valid_1's binary_logloss: 0.478172
[3]	training's binary_logloss: 0.469285	valid_1's binary_logloss: 0.469236
[4]	training's binary_logloss: 0.461184	valid_1's binary_logloss: 0.461671
[5]	training's binary_logloss: 0.454399	valid_1's binary_logloss: 0.455336
[6]	training's binary_logloss: 0.448834	valid_1's binary_logloss: 0.450141
[7]	training's binary_logloss: 0.444138	valid_1's binary_logloss: 0.445973
[8]	training's binary_logloss: 0.440066	valid_1's binary_logloss: 0.442289
[9]	training's binary_logloss: 0.436348	valid_1's binary_logloss: 0.439116
[10]	training's binary_logloss: 0.433137	valid_1's binary_logloss: 0.436381
[11]	training's binary_logloss: 0.429544	valid_1's binary_logloss: 0.433216
[12]	training's binary_logloss: 0.426644	valid_1's binary_logloss: 0.430655
[13]	training's binary_logloss: 0.424071	valid_1's binary_logloss: 0.428487
[14]	training's binar

[109]	training's binary_logloss: 0.319565	valid_1's binary_logloss: 0.348369
[110]	training's binary_logloss: 0.319228	valid_1's binary_logloss: 0.348275
[111]	training's binary_logloss: 0.318734	valid_1's binary_logloss: 0.348059
[112]	training's binary_logloss: 0.318389	valid_1's binary_logloss: 0.347962
[113]	training's binary_logloss: 0.31797	valid_1's binary_logloss: 0.347726
[114]	training's binary_logloss: 0.316899	valid_1's binary_logloss: 0.346834
[115]	training's binary_logloss: 0.316574	valid_1's binary_logloss: 0.346767
[116]	training's binary_logloss: 0.316113	valid_1's binary_logloss: 0.346459
[117]	training's binary_logloss: 0.315606	valid_1's binary_logloss: 0.346148
[118]	training's binary_logloss: 0.315004	valid_1's binary_logloss: 0.345735
[119]	training's binary_logloss: 0.314683	valid_1's binary_logloss: 0.345627
[120]	training's binary_logloss: 0.314325	valid_1's binary_logloss: 0.345548
[121]	training's binary_logloss: 0.313961	valid_1's binary_logloss: 0.345481


[229]	training's binary_logloss: 0.270526	valid_1's binary_logloss: 0.323269
[230]	training's binary_logloss: 0.270248	valid_1's binary_logloss: 0.323252
[231]	training's binary_logloss: 0.269965	valid_1's binary_logloss: 0.323198
[232]	training's binary_logloss: 0.269703	valid_1's binary_logloss: 0.323146
[233]	training's binary_logloss: 0.269249	valid_1's binary_logloss: 0.322908
[234]	training's binary_logloss: 0.269007	valid_1's binary_logloss: 0.322824
[235]	training's binary_logloss: 0.26868	valid_1's binary_logloss: 0.322827
[236]	training's binary_logloss: 0.268447	valid_1's binary_logloss: 0.322844
[237]	training's binary_logloss: 0.267957	valid_1's binary_logloss: 0.322493
[238]	training's binary_logloss: 0.267699	valid_1's binary_logloss: 0.322462
[239]	training's binary_logloss: 0.267339	valid_1's binary_logloss: 0.322327
[240]	training's binary_logloss: 0.267004	valid_1's binary_logloss: 0.322203
[241]	training's binary_logloss: 0.266789	valid_1's binary_logloss: 0.322096


[344]	training's binary_logloss: 0.236881	valid_1's binary_logloss: 0.31107
[345]	training's binary_logloss: 0.23615	valid_1's binary_logloss: 0.310347
[346]	training's binary_logloss: 0.235681	valid_1's binary_logloss: 0.309963
[347]	training's binary_logloss: 0.235464	valid_1's binary_logloss: 0.309938
[348]	training's binary_logloss: 0.235221	valid_1's binary_logloss: 0.309845
[349]	training's binary_logloss: 0.235026	valid_1's binary_logloss: 0.309849
[350]	training's binary_logloss: 0.234731	valid_1's binary_logloss: 0.309659
[351]	training's binary_logloss: 0.234561	valid_1's binary_logloss: 0.309635
[352]	training's binary_logloss: 0.23434	valid_1's binary_logloss: 0.309598
[353]	training's binary_logloss: 0.234137	valid_1's binary_logloss: 0.309585
[354]	training's binary_logloss: 0.233918	valid_1's binary_logloss: 0.30961
[355]	training's binary_logloss: 0.23369	valid_1's binary_logloss: 0.309578
[356]	training's binary_logloss: 0.233406	valid_1's binary_logloss: 0.309524
[357

...

[1242]	training's binary_logloss: 0.105197	valid_1's binary_logloss: 0.281374
[1243]	training's binary_logloss: 0.105086	valid_1's binary_logloss: 0.281313
[1244]	training's binary_logloss: 0.105025	valid_1's binary_logloss: 0.281329
[1245]	training's binary_logloss: 0.10493	valid_1's binary_logloss: 0.281341
[1246]	training's binary_logloss: 0.104837	valid_1's binary_logloss: 0.281345
[1247]	training's binary_logloss: 0.104781	valid_1's binary_logloss: 0.281354
[1248]	training's binary_logloss: 0.104694	valid_1's binary_logloss: 0.281323
[1249]	training's binary_logloss: 0.104611	valid_1's binary_logloss: 0.281324
[1250]	training's binary_logloss: 0.104514	valid_1's binary_logloss: 0.281267
[1251]	training's binary_logloss: 0.104442	valid_1's binary_logloss: 0.281297
[1252]	training's binary_logloss: 0.104357	valid_1's binary_logloss: 0.281293
[1253]	training's binary_logloss: 0.104263	valid_1's binary_logloss: 0.281245
[1254]	training's binary_logloss: 0.104135	valid_1's binary_loglo

[1351]	training's binary_logloss: 0.0957705	valid_1's binary_logloss: 0.279708
[1352]	training's binary_logloss: 0.095694	valid_1's binary_logloss: 0.27973
[1353]	training's binary_logloss: 0.0956155	valid_1's binary_logloss: 0.279767
[1354]	training's binary_logloss: 0.0955265	valid_1's binary_logloss: 0.279752
[1355]	training's binary_logloss: 0.0954324	valid_1's binary_logloss: 0.279779
[1356]	training's binary_logloss: 0.0953756	valid_1's binary_logloss: 0.279825
[1357]	training's binary_logloss: 0.0952956	valid_1's binary_logloss: 0.279802
[1358]	training's binary_logloss: 0.0952201	valid_1's binary_logloss: 0.279777
[1359]	training's binary_logloss: 0.0951524	valid_1's binary_logloss: 0.279801
[1360]	training's binary_logloss: 0.0950264	valid_1's binary_logloss: 0.279651
[1361]	training's binary_logloss: 0.0949216	valid_1's binary_logloss: 0.279583
[1362]	training's binary_logloss: 0.0948413	valid_1's binary_logloss: 0.279631
[1363]	training's binary_logloss: 0.09476	valid_1's bi

[1458]	training's binary_logloss: 0.0872858	valid_1's binary_logloss: 0.278284
[1459]	training's binary_logloss: 0.0872165	valid_1's binary_logloss: 0.278306
[1460]	training's binary_logloss: 0.0871272	valid_1's binary_logloss: 0.278285
[1461]	training's binary_logloss: 0.0870696	valid_1's binary_logloss: 0.278293
[1462]	training's binary_logloss: 0.0869953	valid_1's binary_logloss: 0.278342
[1463]	training's binary_logloss: 0.0869096	valid_1's binary_logloss: 0.278327
[1464]	training's binary_logloss: 0.0868409	valid_1's binary_logloss: 0.278335
[1465]	training's binary_logloss: 0.0867663	valid_1's binary_logloss: 0.27833
[1466]	training's binary_logloss: 0.0867118	valid_1's binary_logloss: 0.278357
[1467]	training's binary_logloss: 0.0866373	valid_1's binary_logloss: 0.27836
[1468]	training's binary_logloss: 0.086556	valid_1's binary_logloss: 0.278356
[1469]	training's binary_logloss: 0.0864894	valid_1's binary_logloss: 0.278368
[1470]	training's binary_logloss: 0.0863786	valid_1's b

[1567]	training's binary_logloss: 0.0798022	valid_1's binary_logloss: 0.277375
[1568]	training's binary_logloss: 0.0797199	valid_1's binary_logloss: 0.277376
[1569]	training's binary_logloss: 0.0796815	valid_1's binary_logloss: 0.27741
[1570]	training's binary_logloss: 0.0795897	valid_1's binary_logloss: 0.277357
[1571]	training's binary_logloss: 0.0795124	valid_1's binary_logloss: 0.277365
[1572]	training's binary_logloss: 0.0794565	valid_1's binary_logloss: 0.277385
[1573]	training's binary_logloss: 0.0793783	valid_1's binary_logloss: 0.277384
[1574]	training's binary_logloss: 0.0793291	valid_1's binary_logloss: 0.277387
[1575]	training's binary_logloss: 0.0792809	valid_1's binary_logloss: 0.277393
[1576]	training's binary_logloss: 0.0792241	valid_1's binary_logloss: 0.277413
[1577]	training's binary_logloss: 0.0791631	valid_1's binary_logloss: 0.277444
[1578]	training's binary_logloss: 0.0790868	valid_1's binary_logloss: 0.277414
[1579]	training's binary_logloss: 0.0790281	valid_1's

[1680]	training's binary_logloss: 0.0730795	valid_1's binary_logloss: 0.278033
[1681]	training's binary_logloss: 0.0730324	valid_1's binary_logloss: 0.278052
[1682]	training's binary_logloss: 0.0729794	valid_1's binary_logloss: 0.278056
[1683]	training's binary_logloss: 0.0729389	valid_1's binary_logloss: 0.278054
[1684]	training's binary_logloss: 0.0728863	valid_1's binary_logloss: 0.278076
[1685]	training's binary_logloss: 0.0728445	valid_1's binary_logloss: 0.278119
[1686]	training's binary_logloss: 0.0727936	valid_1's binary_logloss: 0.278127
[1687]	training's binary_logloss: 0.0727603	valid_1's binary_logloss: 0.278158
[1688]	training's binary_logloss: 0.0727126	valid_1's binary_logloss: 0.278171
[1689]	training's binary_logloss: 0.072641	valid_1's binary_logloss: 0.278217
[1690]	training's binary_logloss: 0.0725867	valid_1's binary_logloss: 0.278233
[1691]	training's binary_logloss: 0.0725224	valid_1's binary_logloss: 0.278164
[1692]	training's binary_logloss: 0.0724627	valid_1's

In [24]:
lgbm_clf = LGBMClassifier(n_estimators=2500, num_leaves=100, subsample=0.6, min_child_samples=110,learning_rate = 0.09,
                          max_depth=148,colsample_bytree= 0.8)

evals = [(X_train, y_train),(X_val, y_val)]
lgbm_clf.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="accuracy", eval_set=evals,
                verbose=True)

preds = lgbm_clf.predict(X_test)
get_clf_eval(y_test, preds)

C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\s\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	training's binary_logloss: 0.494561	valid_1's binary_logloss: 0.493482
[2]	training's binary_logloss: 0.484939	valid_1's binary_logloss: 0.484316
[3]	training's binary_logloss: 0.476992	valid_1's binary_logloss: 0.476746
[4]	training's binary_logloss: 0.469853	valid_1's binary_logloss: 0.469897
[5]	training's binary_logloss: 0.463856	valid_1's binary_logloss: 0.464321
[6]	training's binary_logloss: 0.458728	valid_1's binary_logloss: 0.459451
[7]	training's binary_logloss: 0.454338	valid_1's binary_logloss: 0.455393
[8]	training's binary_logloss: 0.450589	valid_1's binary_logloss: 0.451969
[9]	training's binary_logloss: 0.447077	valid_1's binary_logloss: 0.448761
[10]	training's binary_logloss: 0.443985	valid_1's binary_logloss: 0.446038
[11]	training's binary_logloss: 0.441068	valid_1's binary_logloss: 0.443392
[12]	training's binary_logloss: 0.4384	valid_1's binary_logloss: 0.441027
[13]	training's binary_logloss: 0.435189	valid_1's binary_logloss: 0.438047
[14]	training's binary_

[118]	training's binary_logloss: 0.34021	valid_1's binary_logloss: 0.365192
[119]	training's binary_logloss: 0.339932	valid_1's binary_logloss: 0.365083
[120]	training's binary_logloss: 0.339644	valid_1's binary_logloss: 0.364978
[121]	training's binary_logloss: 0.33937	valid_1's binary_logloss: 0.364875
[122]	training's binary_logloss: 0.338249	valid_1's binary_logloss: 0.363811
[123]	training's binary_logloss: 0.337885	valid_1's binary_logloss: 0.363655
[124]	training's binary_logloss: 0.337427	valid_1's binary_logloss: 0.363436
[125]	training's binary_logloss: 0.337146	valid_1's binary_logloss: 0.363346
[126]	training's binary_logloss: 0.336579	valid_1's binary_logloss: 0.363005
[127]	training's binary_logloss: 0.335246	valid_1's binary_logloss: 0.361748
[128]	training's binary_logloss: 0.335021	valid_1's binary_logloss: 0.361702
[129]	training's binary_logloss: 0.334723	valid_1's binary_logloss: 0.361589
[130]	training's binary_logloss: 0.334315	valid_1's binary_logloss: 0.361411
[

[233]	training's binary_logloss: 0.299039	valid_1's binary_logloss: 0.342254
[234]	training's binary_logloss: 0.298503	valid_1's binary_logloss: 0.341818
[235]	training's binary_logloss: 0.298283	valid_1's binary_logloss: 0.341766
[236]	training's binary_logloss: 0.298051	valid_1's binary_logloss: 0.341712
[237]	training's binary_logloss: 0.297836	valid_1's binary_logloss: 0.341653
[238]	training's binary_logloss: 0.297523	valid_1's binary_logloss: 0.341528
[239]	training's binary_logloss: 0.297304	valid_1's binary_logloss: 0.341463
[240]	training's binary_logloss: 0.297098	valid_1's binary_logloss: 0.341391
[241]	training's binary_logloss: 0.296878	valid_1's binary_logloss: 0.341296
[242]	training's binary_logloss: 0.296109	valid_1's binary_logloss: 0.340488
[243]	training's binary_logloss: 0.295721	valid_1's binary_logloss: 0.340198
[244]	training's binary_logloss: 0.295493	valid_1's binary_logloss: 0.340161
[245]	training's binary_logloss: 0.295254	valid_1's binary_logloss: 0.340068

[340]	training's binary_logloss: 0.271628	valid_1's binary_logloss: 0.329174
[341]	training's binary_logloss: 0.271413	valid_1's binary_logloss: 0.329051
[342]	training's binary_logloss: 0.271211	valid_1's binary_logloss: 0.32898
[343]	training's binary_logloss: 0.27098	valid_1's binary_logloss: 0.328935
[344]	training's binary_logloss: 0.270717	valid_1's binary_logloss: 0.328805
[345]	training's binary_logloss: 0.270538	valid_1's binary_logloss: 0.328715
[346]	training's binary_logloss: 0.270297	valid_1's binary_logloss: 0.328601
[347]	training's binary_logloss: 0.270145	valid_1's binary_logloss: 0.32859
[348]	training's binary_logloss: 0.269774	valid_1's binary_logloss: 0.328325
[349]	training's binary_logloss: 0.26959	valid_1's binary_logloss: 0.328319
[350]	training's binary_logloss: 0.269317	valid_1's binary_logloss: 0.3282
[351]	training's binary_logloss: 0.26917	valid_1's binary_logloss: 0.328186
[352]	training's binary_logloss: 0.269025	valid_1's binary_logloss: 0.328159
[353]	

...

[1579]	training's binary_logloss: 0.118398	valid_1's binary_logloss: 0.285176
[1580]	training's binary_logloss: 0.118323	valid_1's binary_logloss: 0.285172
[1581]	training's binary_logloss: 0.118214	valid_1's binary_logloss: 0.285114
[1582]	training's binary_logloss: 0.11816	valid_1's binary_logloss: 0.285112
[1583]	training's binary_logloss: 0.118093	valid_1's binary_logloss: 0.285124
[1584]	training's binary_logloss: 0.118036	valid_1's binary_logloss: 0.285124
[1585]	training's binary_logloss: 0.117971	valid_1's binary_logloss: 0.285129
[1586]	training's binary_logloss: 0.117916	valid_1's binary_logloss: 0.285163
[1587]	training's binary_logloss: 0.117847	valid_1's binary_logloss: 0.285179
[1588]	training's binary_logloss: 0.11778	valid_1's binary_logloss: 0.285181
[1589]	training's binary_logloss: 0.117687	valid_1's binary_logloss: 0.28516
[1590]	training's binary_logloss: 0.117564	valid_1's binary_logloss: 0.285048
[1591]	training's binary_logloss: 0.11751	valid_1's binary_logloss:

[1697]	training's binary_logloss: 0.110124	valid_1's binary_logloss: 0.283076
[1698]	training's binary_logloss: 0.110082	valid_1's binary_logloss: 0.283065
[1699]	training's binary_logloss: 0.110016	valid_1's binary_logloss: 0.283089
[1700]	training's binary_logloss: 0.109962	valid_1's binary_logloss: 0.283098
[1701]	training's binary_logloss: 0.10991	valid_1's binary_logloss: 0.283096
[1702]	training's binary_logloss: 0.109861	valid_1's binary_logloss: 0.283079
[1703]	training's binary_logloss: 0.109742	valid_1's binary_logloss: 0.282952
[1704]	training's binary_logloss: 0.109669	valid_1's binary_logloss: 0.282922
[1705]	training's binary_logloss: 0.109602	valid_1's binary_logloss: 0.282932
[1706]	training's binary_logloss: 0.109546	valid_1's binary_logloss: 0.282929
[1707]	training's binary_logloss: 0.109492	valid_1's binary_logloss: 0.282953
[1708]	training's binary_logloss: 0.109443	valid_1's binary_logloss: 0.282976
[1709]	training's binary_logloss: 0.109403	valid_1's binary_loglo

[1811]	training's binary_logloss: 0.103043	valid_1's binary_logloss: 0.282528
[1812]	training's binary_logloss: 0.102984	valid_1's binary_logloss: 0.282524
[1813]	training's binary_logloss: 0.102924	valid_1's binary_logloss: 0.282498
[1814]	training's binary_logloss: 0.102869	valid_1's binary_logloss: 0.282515
[1815]	training's binary_logloss: 0.1028	valid_1's binary_logloss: 0.282515
[1816]	training's binary_logloss: 0.102768	valid_1's binary_logloss: 0.282541
[1817]	training's binary_logloss: 0.102712	valid_1's binary_logloss: 0.282533
[1818]	training's binary_logloss: 0.102649	valid_1's binary_logloss: 0.282559
[1819]	training's binary_logloss: 0.10259	valid_1's binary_logloss: 0.282569
[1820]	training's binary_logloss: 0.102525	valid_1's binary_logloss: 0.282598
[1821]	training's binary_logloss: 0.102473	valid_1's binary_logloss: 0.282615
[1822]	training's binary_logloss: 0.102419	valid_1's binary_logloss: 0.282613
[1823]	training's binary_logloss: 0.102368	valid_1's binary_logloss

[1921]	training's binary_logloss: 0.0967849	valid_1's binary_logloss: 0.282082
[1922]	training's binary_logloss: 0.0967288	valid_1's binary_logloss: 0.282099
[1923]	training's binary_logloss: 0.0966878	valid_1's binary_logloss: 0.282127
[1924]	training's binary_logloss: 0.0965932	valid_1's binary_logloss: 0.282
[1925]	training's binary_logloss: 0.096535	valid_1's binary_logloss: 0.282006
[1926]	training's binary_logloss: 0.096478	valid_1's binary_logloss: 0.281994
[1927]	training's binary_logloss: 0.0964315	valid_1's binary_logloss: 0.281997
[1928]	training's binary_logloss: 0.0963631	valid_1's binary_logloss: 0.281976
[1929]	training's binary_logloss: 0.0963083	valid_1's binary_logloss: 0.281989
[1930]	training's binary_logloss: 0.0962622	valid_1's binary_logloss: 0.28197
[1931]	training's binary_logloss: 0.0962181	valid_1's binary_logloss: 0.281977
[1932]	training's binary_logloss: 0.0961489	valid_1's binary_logloss: 0.281938
[1933]	training's binary_logloss: 0.0960977	valid_1's bina

[2027]	training's binary_logloss: 0.0909917	valid_1's binary_logloss: 0.281866
[2028]	training's binary_logloss: 0.0909423	valid_1's binary_logloss: 0.281881
[2029]	training's binary_logloss: 0.0908908	valid_1's binary_logloss: 0.281871
[2030]	training's binary_logloss: 0.0908514	valid_1's binary_logloss: 0.281883
[2031]	training's binary_logloss: 0.0907934	valid_1's binary_logloss: 0.281869
[2032]	training's binary_logloss: 0.0907634	valid_1's binary_logloss: 0.281891
[2033]	training's binary_logloss: 0.0907222	valid_1's binary_logloss: 0.281913
[2034]	training's binary_logloss: 0.0906604	valid_1's binary_logloss: 0.281865
[2035]	training's binary_logloss: 0.0905829	valid_1's binary_logloss: 0.281831
[2036]	training's binary_logloss: 0.0905321	valid_1's binary_logloss: 0.281836
[2037]	training's binary_logloss: 0.0904885	valid_1's binary_logloss: 0.281838
[2038]	training's binary_logloss: 0.0904455	valid_1's binary_logloss: 0.281867
[2039]	training's binary_logloss: 0.0904056	valid_1'

In [9]:
lgbm_clf = LGBMClassifier(n_estimators=2000, num_leaves=100, subsample=0.6, min_child_samples=80,learning_rate = 0.12,
                          max_depth=128,colsample_bytree= 0.8)

evals = [(X_train, y_train),(X_val, y_val)]
lgbm_clf.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="accuracy", eval_set=evals,
                verbose=True)

preds = lgbm_clf.predict(X_test)
get_clf_eval(y_test, preds)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	training's binary_logloss: 0.490846	valid_1's binary_logloss: 0.489954
[2]	training's binary_logloss: 0.478966	valid_1's binary_logloss: 0.478789
[3]	training's binary_logloss: 0.469751	valid_1's binary_logloss: 0.470058
[4]	training's binary_logloss: 0.461784	valid_1's binary_logloss: 0.462448
[5]	training's binary_logloss: 0.455495	valid_1's binary_logloss: 0.456601
[6]	training's binary_logloss: 0.450105	valid_1's binary_logloss: 0.451629
[7]	training's binary_logloss: 0.445322	valid_1's binary_logloss: 0.447218
[8]	training's binary_logloss: 0.441616	valid_1's binary_logloss: 0.44383
[9]	training's binary_logloss: 0.438205	valid_1's binary_logloss: 0.44089
[10]	training's binary_logloss: 0.435035	valid_1's binary_logloss: 0.438128
[11]	training's binary_logloss: 0.431884	valid_1's binary_logloss: 0.435266
[12]	training's binary_logloss: 0.429029	valid_1's binary_logloss: 0.432775
[13]	training's binary_logloss: 0.426237	valid_1's binary_logloss: 0.430416
[14]	training's binary_

[114]	training's binary_logloss: 0.320006	valid_1's binary_logloss: 0.351011
[115]	training's binary_logloss: 0.319683	valid_1's binary_logloss: 0.350901
[116]	training's binary_logloss: 0.318946	valid_1's binary_logloss: 0.350276
[117]	training's binary_logloss: 0.318555	valid_1's binary_logloss: 0.350054
[118]	training's binary_logloss: 0.317673	valid_1's binary_logloss: 0.349358
[119]	training's binary_logloss: 0.317141	valid_1's binary_logloss: 0.349122
[120]	training's binary_logloss: 0.316824	valid_1's binary_logloss: 0.349026
[121]	training's binary_logloss: 0.316221	valid_1's binary_logloss: 0.348588
[122]	training's binary_logloss: 0.315929	valid_1's binary_logloss: 0.348555
[123]	training's binary_logloss: 0.315598	valid_1's binary_logloss: 0.3485
[124]	training's binary_logloss: 0.314977	valid_1's binary_logloss: 0.348098
[125]	training's binary_logloss: 0.314617	valid_1's binary_logloss: 0.347936
[126]	training's binary_logloss: 0.313808	valid_1's binary_logloss: 0.347306
[

[233]	training's binary_logloss: 0.272019	valid_1's binary_logloss: 0.325853
[234]	training's binary_logloss: 0.271783	valid_1's binary_logloss: 0.325839
[235]	training's binary_logloss: 0.271325	valid_1's binary_logloss: 0.325498
[236]	training's binary_logloss: 0.271034	valid_1's binary_logloss: 0.32546
[237]	training's binary_logloss: 0.270785	valid_1's binary_logloss: 0.325432
[238]	training's binary_logloss: 0.270583	valid_1's binary_logloss: 0.325367
[239]	training's binary_logloss: 0.270347	valid_1's binary_logloss: 0.325255
[240]	training's binary_logloss: 0.269574	valid_1's binary_logloss: 0.324541
[241]	training's binary_logloss: 0.268983	valid_1's binary_logloss: 0.324162
[242]	training's binary_logloss: 0.26836	valid_1's binary_logloss: 0.323602
[243]	training's binary_logloss: 0.268079	valid_1's binary_logloss: 0.323583
[244]	training's binary_logloss: 0.267904	valid_1's binary_logloss: 0.323598
[245]	training's binary_logloss: 0.267661	valid_1's binary_logloss: 0.323544
[

[346]	training's binary_logloss: 0.24038	valid_1's binary_logloss: 0.313669
[347]	training's binary_logloss: 0.24008	valid_1's binary_logloss: 0.313542
[348]	training's binary_logloss: 0.23983	valid_1's binary_logloss: 0.31349
[349]	training's binary_logloss: 0.239668	valid_1's binary_logloss: 0.313496
[350]	training's binary_logloss: 0.239447	valid_1's binary_logloss: 0.313484
[351]	training's binary_logloss: 0.239228	valid_1's binary_logloss: 0.313445
[352]	training's binary_logloss: 0.239004	valid_1's binary_logloss: 0.313456
[353]	training's binary_logloss: 0.238819	valid_1's binary_logloss: 0.31343
[354]	training's binary_logloss: 0.238651	valid_1's binary_logloss: 0.313445
[355]	training's binary_logloss: 0.238493	valid_1's binary_logloss: 0.313424
[356]	training's binary_logloss: 0.238301	valid_1's binary_logloss: 0.313413
[357]	training's binary_logloss: 0.237912	valid_1's binary_logloss: 0.313159
[358]	training's binary_logloss: 0.23774	valid_1's binary_logloss: 0.313094
[359]

...

[1130]	training's binary_logloss: 0.120177	valid_1's binary_logloss: 0.285228
[1131]	training's binary_logloss: 0.120082	valid_1's binary_logloss: 0.28527
[1132]	training's binary_logloss: 0.11996	valid_1's binary_logloss: 0.285241
[1133]	training's binary_logloss: 0.119898	valid_1's binary_logloss: 0.285275
[1134]	training's binary_logloss: 0.119826	valid_1's binary_logloss: 0.285288
[1135]	training's binary_logloss: 0.119774	valid_1's binary_logloss: 0.285287
[1136]	training's binary_logloss: 0.119681	valid_1's binary_logloss: 0.285296
[1137]	training's binary_logloss: 0.119592	valid_1's binary_logloss: 0.2853
[1138]	training's binary_logloss: 0.119545	valid_1's binary_logloss: 0.285308
[1139]	training's binary_logloss: 0.119456	valid_1's binary_logloss: 0.285333
[1140]	training's binary_logloss: 0.11936	valid_1's binary_logloss: 0.285354
[1141]	training's binary_logloss: 0.119208	valid_1's binary_logloss: 0.285311
[1142]	training's binary_logloss: 0.119114	valid_1's binary_logloss: 

[1239]	training's binary_logloss: 0.109576	valid_1's binary_logloss: 0.283469
[1240]	training's binary_logloss: 0.109472	valid_1's binary_logloss: 0.283401
[1241]	training's binary_logloss: 0.10939	valid_1's binary_logloss: 0.283397
[1242]	training's binary_logloss: 0.109261	valid_1's binary_logloss: 0.283361
[1243]	training's binary_logloss: 0.109097	valid_1's binary_logloss: 0.283161
[1244]	training's binary_logloss: 0.109	valid_1's binary_logloss: 0.283154
[1245]	training's binary_logloss: 0.108904	valid_1's binary_logloss: 0.283063
[1246]	training's binary_logloss: 0.10882	valid_1's binary_logloss: 0.283074
[1247]	training's binary_logloss: 0.108731	valid_1's binary_logloss: 0.28301
[1248]	training's binary_logloss: 0.108649	valid_1's binary_logloss: 0.282998
[1249]	training's binary_logloss: 0.108489	valid_1's binary_logloss: 0.282859
[1250]	training's binary_logloss: 0.10841	valid_1's binary_logloss: 0.282861
[1251]	training's binary_logloss: 0.108333	valid_1's binary_logloss: 0.

[1353]	training's binary_logloss: 0.100209	valid_1's binary_logloss: 0.283014
[1354]	training's binary_logloss: 0.10013	valid_1's binary_logloss: 0.283073
[1355]	training's binary_logloss: 0.100047	valid_1's binary_logloss: 0.28307
[1356]	training's binary_logloss: 0.0999651	valid_1's binary_logloss: 0.283073
[1357]	training's binary_logloss: 0.0998772	valid_1's binary_logloss: 0.283065
[1358]	training's binary_logloss: 0.0998103	valid_1's binary_logloss: 0.283074
[1359]	training's binary_logloss: 0.0996684	valid_1's binary_logloss: 0.282975
[1360]	training's binary_logloss: 0.0995691	valid_1's binary_logloss: 0.282913
[1361]	training's binary_logloss: 0.0994665	valid_1's binary_logloss: 0.28281
[1362]	training's binary_logloss: 0.0993841	valid_1's binary_logloss: 0.282814
[1363]	training's binary_logloss: 0.0993071	valid_1's binary_logloss: 0.282799
[1364]	training's binary_logloss: 0.0992478	valid_1's binary_logloss: 0.282798
[1365]	training's binary_logloss: 0.0991732	valid_1's bina

[1459]	training's binary_logloss: 0.0915284	valid_1's binary_logloss: 0.281626
[1460]	training's binary_logloss: 0.0914653	valid_1's binary_logloss: 0.281648
[1461]	training's binary_logloss: 0.0914079	valid_1's binary_logloss: 0.281663
[1462]	training's binary_logloss: 0.0913452	valid_1's binary_logloss: 0.281661
[1463]	training's binary_logloss: 0.0912838	valid_1's binary_logloss: 0.281674
[1464]	training's binary_logloss: 0.0911388	valid_1's binary_logloss: 0.281541
[1465]	training's binary_logloss: 0.0910532	valid_1's binary_logloss: 0.281455
[1466]	training's binary_logloss: 0.0909874	valid_1's binary_logloss: 0.28147
[1467]	training's binary_logloss: 0.0908982	valid_1's binary_logloss: 0.281455
[1468]	training's binary_logloss: 0.0907807	valid_1's binary_logloss: 0.281341
[1469]	training's binary_logloss: 0.0906036	valid_1's binary_logloss: 0.281135
[1470]	training's binary_logloss: 0.0905105	valid_1's binary_logloss: 0.281191
[1471]	training's binary_logloss: 0.0904361	valid_1's

[1571]	training's binary_logloss: 0.0838756	valid_1's binary_logloss: 0.281092
[1572]	training's binary_logloss: 0.0838373	valid_1's binary_logloss: 0.281102
[1573]	training's binary_logloss: 0.0837752	valid_1's binary_logloss: 0.281116
[1574]	training's binary_logloss: 0.0837023	valid_1's binary_logloss: 0.281109
[1575]	training's binary_logloss: 0.0836598	valid_1's binary_logloss: 0.281132
[1576]	training's binary_logloss: 0.0835923	valid_1's binary_logloss: 0.281139
[1577]	training's binary_logloss: 0.0835184	valid_1's binary_logloss: 0.281139
[1578]	training's binary_logloss: 0.0834517	valid_1's binary_logloss: 0.28116
[1579]	training's binary_logloss: 0.0833557	valid_1's binary_logloss: 0.281119
[1580]	training's binary_logloss: 0.0832962	valid_1's binary_logloss: 0.281144
[1581]	training's binary_logloss: 0.0832472	valid_1's binary_logloss: 0.281158
[1582]	training's binary_logloss: 0.0831865	valid_1's binary_logloss: 0.281155
[1583]	training's binary_logloss: 0.0831373	valid_1's

In [5]:
from sklearn.model_selection import GridSearchCV

# 하이퍼 파라미터 테스트의 수행 속도를 향상시키기 위해 n_estimators를 100으로 감소
lgbm_wrapper = LGBMClassifier(n_estimators=200)

params = {'learnig_rate':[0.1, 0.5,0.8] ,'max_depth': [3,5,7,128],'num_leaves':[31,15,64],'min_child_samples':[60,100],
          'subsample': [0.8,1]}

# cv는 3으로 지정 
gridcv = GridSearchCV(lgbm_wrapper, param_grid=params, cv=2)
gridcv.fit(X_train, y_train, early_stopping_rounds=30, eval_metric="error",
           eval_set=[(X_val,y_val)])

print('GridSearchCV 최적 파라미터:',gridcv.best_params_) 

xgb_roc_score = roc_auc_score(y_test, gridcv.predict_proba(X_test)[:,1], average='macro')
print('ROC AUC: {0:.4f}'.format(xgb_roc_score))

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Warning] Unknown parameter: learnig_rate
[1]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.494812
[2]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.488103
[3]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.482441
[4]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.478081
[5]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.474539
[6]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.471398
[7]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.468859
[8]	valid_0's binary_error: 0.20228	valid_0's binary_logloss: 0.46673
[9]	valid_0's binary_error: 0.202098	valid_0's binary_logloss: 0.465011
[10]	valid_0's binary_error: 0.202026	valid_0's binary_logloss: 0.463406
[11]	valid_0's binary_error: 0.20128	valid_0's binary_logloss: 0.461969
[12]	valid_0's binary_error: 0.200207	valid_0's binary_logloss: 0.460405
[13]	valid_0's binary_error: 0.19968	valid_0's binary_logloss: 0.459202
[14]	valid_0's bin

[119]	valid_0's binary_error: 0.186842	valid_0's binary_logloss: 0.429957
[120]	valid_0's binary_error: 0.186696	valid_0's binary_logloss: 0.429919
[121]	valid_0's binary_error: 0.186624	valid_0's binary_logloss: 0.429879
[122]	valid_0's binary_error: 0.186606	valid_0's binary_logloss: 0.429626
[123]	valid_0's binary_error: 0.186569	valid_0's binary_logloss: 0.429462
[124]	valid_0's binary_error: 0.186624	valid_0's binary_logloss: 0.429395
[125]	valid_0's binary_error: 0.186751	valid_0's binary_logloss: 0.4291
[126]	valid_0's binary_error: 0.186715	valid_0's binary_logloss: 0.428985
[127]	valid_0's binary_error: 0.186733	valid_0's binary_logloss: 0.42876
[128]	valid_0's binary_error: 0.186769	valid_0's binary_logloss: 0.428664
[129]	valid_0's binary_error: 0.186715	valid_0's binary_logloss: 0.428649
[130]	valid_0's binary_error: 0.186642	valid_0's binary_logloss: 0.428566
[131]	valid_0's binary_error: 0.186515	valid_0's binary_logloss: 0.42832
[132]	valid_0's binary_error: 0.186406	val

[164]	valid_0's binary_error: 0.185878	valid_0's binary_logloss: 0.425012
[165]	valid_0's binary_error: 0.185769	valid_0's binary_logloss: 0.424984
[166]	valid_0's binary_error: 0.185678	valid_0's binary_logloss: 0.42495
[167]	valid_0's binary_error: 0.185569	valid_0's binary_logloss: 0.424734
[168]	valid_0's binary_error: 0.185678	valid_0's binary_logloss: 0.424668
[169]	valid_0's binary_error: 0.185715	valid_0's binary_logloss: 0.424597
[170]	valid_0's binary_error: 0.18566	valid_0's binary_logloss: 0.424532
[171]	valid_0's binary_error: 0.185624	valid_0's binary_logloss: 0.424383
[172]	valid_0's binary_error: 0.185515	valid_0's binary_logloss: 0.424329
[173]	valid_0's binary_error: 0.185569	valid_0's binary_logloss: 0.42428
[174]	valid_0's binary_error: 0.185605	valid_0's binary_logloss: 0.42418
[175]	valid_0's binary_error: 0.185551	valid_0's binary_logloss: 0.424076
[176]	valid_0's binary_error: 0.185533	valid_0's binary_logloss: 0.424046
[177]	valid_0's binary_error: 0.185569	val

[97]	valid_0's binary_error: 0.187969	valid_0's binary_logloss: 0.432384
[98]	valid_0's binary_error: 0.187824	valid_0's binary_logloss: 0.432293
[99]	valid_0's binary_error: 0.187915	valid_0's binary_logloss: 0.432256
[100]	valid_0's binary_error: 0.187842	valid_0's binary_logloss: 0.432166
[101]	valid_0's binary_error: 0.187951	valid_0's binary_logloss: 0.432132
[102]	valid_0's binary_error: 0.187751	valid_0's binary_logloss: 0.432081
[103]	valid_0's binary_error: 0.187697	valid_0's binary_logloss: 0.431986
[104]	valid_0's binary_error: 0.187678	valid_0's binary_logloss: 0.431823
[105]	valid_0's binary_error: 0.187551	valid_0's binary_logloss: 0.431736
[106]	valid_0's binary_error: 0.187297	valid_0's binary_logloss: 0.431467
[107]	valid_0's binary_error: 0.187133	valid_0's binary_logloss: 0.431357
[108]	valid_0's binary_error: 0.187115	valid_0's binary_logloss: 0.431257
[109]	valid_0's binary_error: 0.187097	valid_0's binary_logloss: 0.430959
[110]	valid_0's binary_error: 0.187133	va

...

[139]	valid_0's binary_error: 0.166512	valid_0's binary_logloss: 0.376892
[140]	valid_0's binary_error: 0.166512	valid_0's binary_logloss: 0.376732
[141]	valid_0's binary_error: 0.166039	valid_0's binary_logloss: 0.37584
[142]	valid_0's binary_error: 0.166094	valid_0's binary_logloss: 0.375773
[143]	valid_0's binary_error: 0.166003	valid_0's binary_logloss: 0.375674
[144]	valid_0's binary_error: 0.165967	valid_0's binary_logloss: 0.375646
[145]	valid_0's binary_error: 0.165967	valid_0's binary_logloss: 0.375516
[146]	valid_0's binary_error: 0.16593	valid_0's binary_logloss: 0.375498
[147]	valid_0's binary_error: 0.166076	valid_0's binary_logloss: 0.375454
[148]	valid_0's binary_error: 0.166057	valid_0's binary_logloss: 0.375464
[149]	valid_0's binary_error: 0.166094	valid_0's binary_logloss: 0.375461
[150]	valid_0's binary_error: 0.165985	valid_0's binary_logloss: 0.37541
[151]	valid_0's binary_error: 0.166021	valid_0's binary_logloss: 0.375199
[152]	valid_0's binary_error: 0.165603	va

[54]	valid_0's binary_error: 0.176732	valid_0's binary_logloss: 0.401578
[55]	valid_0's binary_error: 0.176513	valid_0's binary_logloss: 0.401348
[56]	valid_0's binary_error: 0.176204	valid_0's binary_logloss: 0.401091
[57]	valid_0's binary_error: 0.175786	valid_0's binary_logloss: 0.400315
[58]	valid_0's binary_error: 0.175077	valid_0's binary_logloss: 0.399239
[59]	valid_0's binary_error: 0.174768	valid_0's binary_logloss: 0.398538
[60]	valid_0's binary_error: 0.174604	valid_0's binary_logloss: 0.398206
[61]	valid_0's binary_error: 0.174513	valid_0's binary_logloss: 0.397974
[62]	valid_0's binary_error: 0.174513	valid_0's binary_logloss: 0.397728
[63]	valid_0's binary_error: 0.174549	valid_0's binary_logloss: 0.397367
[64]	valid_0's binary_error: 0.174531	valid_0's binary_logloss: 0.397229
[65]	valid_0's binary_error: 0.174422	valid_0's binary_logloss: 0.396988
[66]	valid_0's binary_error: 0.174259	valid_0's binary_logloss: 0.39662
[67]	valid_0's binary_error: 0.174113	valid_0's bina

[167]	valid_0's binary_error: 0.161821	valid_0's binary_logloss: 0.367405
[168]	valid_0's binary_error: 0.161893	valid_0's binary_logloss: 0.367266
[169]	valid_0's binary_error: 0.161893	valid_0's binary_logloss: 0.367242
[170]	valid_0's binary_error: 0.161893	valid_0's binary_logloss: 0.367193
[171]	valid_0's binary_error: 0.161821	valid_0's binary_logloss: 0.367163
[172]	valid_0's binary_error: 0.161839	valid_0's binary_logloss: 0.367143
[173]	valid_0's binary_error: 0.162039	valid_0's binary_logloss: 0.367061
[174]	valid_0's binary_error: 0.161948	valid_0's binary_logloss: 0.366978
[175]	valid_0's binary_error: 0.161875	valid_0's binary_logloss: 0.366956
[176]	valid_0's binary_error: 0.161766	valid_0's binary_logloss: 0.367001
[177]	valid_0's binary_error: 0.161184	valid_0's binary_logloss: 0.366202
[178]	valid_0's binary_error: 0.161039	valid_0's binary_logloss: 0.366091
[179]	valid_0's binary_error: 0.161166	valid_0's binary_logloss: 0.366024
[180]	valid_0's binary_error: 0.161111

[86]	valid_0's binary_error: 0.166203	valid_0's binary_logloss: 0.381093
[87]	valid_0's binary_error: 0.165967	valid_0's binary_logloss: 0.380408
[88]	valid_0's binary_error: 0.165985	valid_0's binary_logloss: 0.380163
[89]	valid_0's binary_error: 0.16593	valid_0's binary_logloss: 0.380032
[90]	valid_0's binary_error: 0.165494	valid_0's binary_logloss: 0.379747
[91]	valid_0's binary_error: 0.165276	valid_0's binary_logloss: 0.379324
[92]	valid_0's binary_error: 0.165257	valid_0's binary_logloss: 0.379178
[93]	valid_0's binary_error: 0.165039	valid_0's binary_logloss: 0.378339
[94]	valid_0's binary_error: 0.164912	valid_0's binary_logloss: 0.378112
[95]	valid_0's binary_error: 0.164803	valid_0's binary_logloss: 0.377825
[96]	valid_0's binary_error: 0.164475	valid_0's binary_logloss: 0.376967
[97]	valid_0's binary_error: 0.164457	valid_0's binary_logloss: 0.3767
[98]	valid_0's binary_error: 0.164257	valid_0's binary_logloss: 0.376577
[99]	valid_0's binary_error: 0.164057	valid_0's binary

ROC AUC: 0.8703


In [12]:
lgbm_wrapper = LGBMClassifier(n_estimators=200,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

In [13]:
lgbm_wrapper = LGBMClassifier(n_estimators=400,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[215]	valid_0's binary_logloss: 0.347188
[216]	valid_0's binary_logloss: 0.346953
[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's binary_logloss: 0.342194
[234]	valid_0's binary_logloss: 0.341976
[235]	valid_0's binary_logloss: 0.341697
[236]	valid_0's binary_logloss: 0.341234
[237]	valid_0's binary_logloss: 0.341206
[238]	valid_0's binary_logloss: 0.341152
[239]	valid_0's b

In [14]:
lgbm_wrapper = LGBMClassifier(n_estimators=800,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's binary_logloss: 0.342194
[234]	valid_0's binary_logloss: 0.341976
[235]	valid_0's binary_logloss: 0.341697
[236]	valid_0's binary_logloss: 0.341234
[237]	valid_0's binary_logloss: 0.341206
[238]	valid_0's binary_logloss: 0.341152
[239]	valid_0's binary_logloss: 0.341113
[240]	valid_0's binary_logloss: 0.340959
[241]	valid_0's b

[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binary_logloss: 0.320492
[438]	valid_0's binary_logloss: 0.320435
[439]	valid_0's binary_logloss: 0.320437
[440]	valid_0's binary_logloss: 0.320403
[441]	valid_0's binary_logloss: 0.320275
[442]	valid_0's binary_logloss: 0.320276
[443]	valid_0's binary_logloss: 0.320231
[444]	valid_0's binary_logloss: 0.320142
[445]	valid_0's binary_logloss: 0.320124
[446]	valid_0's binary_logloss: 0.320138
[447]	valid_0's binary_logloss: 0.31984
[448]	valid_0's binary_logloss: 0.319772
[449]	valid_0's binary_logloss: 0.319567
[450]	valid_0's binary_logloss: 0.319456
[451]	valid_0's binary_logloss: 0.319465
[452]	valid_0's binary_logloss: 0.3194
[453]	valid_0's binary_logloss: 0.319373
[454]	valid_0's binary_logloss: 0.319261
[455]	valid_0's binary_logloss: 0.319262
[456]	valid_0's binary_logloss: 0.319089
[457]	valid_0's binary_logloss: 0.318805
[458]	valid_0's binary_logloss: 0.318779
[459]	valid_0's bin

[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's binary_logloss: 0.307378
[650]	valid_0's binary_logloss: 0.307251
[651]	valid_0's binary_logloss: 0.30716
[652]	valid_0's binary_logloss: 0.307154
[653]	valid_0's binary_logloss: 0.307141
[654]	valid_0's binary_logloss: 0.307073
[655]	valid_0's binary_logloss: 0.307
[656]	valid_0's binary_logloss: 0.306996
[657]	valid_0's binary_logloss: 0.306976
[658]	valid_0's binary_logloss: 0.306941
[659]	valid_0's binary_logloss: 0.306941
[660]	valid_0's binary_logloss: 0.306835
[661]	valid_0's binary_logloss: 0.306767
[662]	valid_0's binary_logloss: 0.306707
[663]	valid_0's binary_logloss: 0.306667
[664]	valid_0's binary_logloss: 0.306667
[665]	valid_0's binary

In [15]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[214]	valid_0's binary_logloss: 0.347206
[215]	valid_0's binary_logloss: 0.347188
[216]	valid_0's binary_logloss: 0.346953
[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's binary_logloss: 0.342194
[234]	valid_0's binary_logloss: 0.341976
[235]	valid_0's binary_logloss: 0.341697
[236]	valid_0's binary_logloss: 0.341234
[237]	valid_0's binary_logloss: 0.341206
[238]	valid_0's b

[415]	valid_0's binary_logloss: 0.322037
[416]	valid_0's binary_logloss: 0.322036
[417]	valid_0's binary_logloss: 0.321957
[418]	valid_0's binary_logloss: 0.321848
[419]	valid_0's binary_logloss: 0.321622
[420]	valid_0's binary_logloss: 0.32162
[421]	valid_0's binary_logloss: 0.321616
[422]	valid_0's binary_logloss: 0.321623
[423]	valid_0's binary_logloss: 0.321591
[424]	valid_0's binary_logloss: 0.321599
[425]	valid_0's binary_logloss: 0.321356
[426]	valid_0's binary_logloss: 0.321213
[427]	valid_0's binary_logloss: 0.320967
[428]	valid_0's binary_logloss: 0.32078
[429]	valid_0's binary_logloss: 0.32081
[430]	valid_0's binary_logloss: 0.320775
[431]	valid_0's binary_logloss: 0.320763
[432]	valid_0's binary_logloss: 0.320721
[433]	valid_0's binary_logloss: 0.320712
[434]	valid_0's binary_logloss: 0.32052
[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binary_logloss: 0.320492
[438]	valid_0's binary_logloss: 0.320435
[439]	valid_0's bina

[625]	valid_0's binary_logloss: 0.308154
[626]	valid_0's binary_logloss: 0.308127
[627]	valid_0's binary_logloss: 0.308101
[628]	valid_0's binary_logloss: 0.30812
[629]	valid_0's binary_logloss: 0.308098
[630]	valid_0's binary_logloss: 0.308107
[631]	valid_0's binary_logloss: 0.308099
[632]	valid_0's binary_logloss: 0.308108
[633]	valid_0's binary_logloss: 0.308122
[634]	valid_0's binary_logloss: 0.307943
[635]	valid_0's binary_logloss: 0.30794
[636]	valid_0's binary_logloss: 0.307838
[637]	valid_0's binary_logloss: 0.307805
[638]	valid_0's binary_logloss: 0.307797
[639]	valid_0's binary_logloss: 0.307798
[640]	valid_0's binary_logloss: 0.307776
[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's bina

[827]	valid_0's binary_logloss: 0.300806
[828]	valid_0's binary_logloss: 0.300819
[829]	valid_0's binary_logloss: 0.300634
[830]	valid_0's binary_logloss: 0.300577
[831]	valid_0's binary_logloss: 0.3006
[832]	valid_0's binary_logloss: 0.30056
[833]	valid_0's binary_logloss: 0.300573
[834]	valid_0's binary_logloss: 0.300511
[835]	valid_0's binary_logloss: 0.300513
[836]	valid_0's binary_logloss: 0.300444
[837]	valid_0's binary_logloss: 0.30045
[838]	valid_0's binary_logloss: 0.30044
[839]	valid_0's binary_logloss: 0.300335
[840]	valid_0's binary_logloss: 0.300313
[841]	valid_0's binary_logloss: 0.30033
[842]	valid_0's binary_logloss: 0.300335
[843]	valid_0's binary_logloss: 0.300339
[844]	valid_0's binary_logloss: 0.300228
[845]	valid_0's binary_logloss: 0.300209
[846]	valid_0's binary_logloss: 0.300225
[847]	valid_0's binary_logloss: 0.300237
[848]	valid_0's binary_logloss: 0.299943
[849]	valid_0's binary_logloss: 0.29995
[850]	valid_0's binary_logloss: 0.299968
[851]	valid_0's binary_

[1054]	valid_0's binary_logloss: 0.294733
[1055]	valid_0's binary_logloss: 0.294729
[1056]	valid_0's binary_logloss: 0.294748
[1057]	valid_0's binary_logloss: 0.294711
[1058]	valid_0's binary_logloss: 0.294648
[1059]	valid_0's binary_logloss: 0.294646
[1060]	valid_0's binary_logloss: 0.294631
[1061]	valid_0's binary_logloss: 0.294635
[1062]	valid_0's binary_logloss: 0.294625
[1063]	valid_0's binary_logloss: 0.294478
[1064]	valid_0's binary_logloss: 0.294379
[1065]	valid_0's binary_logloss: 0.294359
[1066]	valid_0's binary_logloss: 0.294355
[1067]	valid_0's binary_logloss: 0.294378
[1068]	valid_0's binary_logloss: 0.29438
[1069]	valid_0's binary_logloss: 0.294378
[1070]	valid_0's binary_logloss: 0.294331
[1071]	valid_0's binary_logloss: 0.294356
[1072]	valid_0's binary_logloss: 0.294286
[1073]	valid_0's binary_logloss: 0.294291
[1074]	valid_0's binary_logloss: 0.294313
[1075]	valid_0's binary_logloss: 0.294328
[1076]	valid_0's binary_logloss: 0.294286
[1077]	valid_0's binary_logloss: 0.

[1251]	valid_0's binary_logloss: 0.291766
[1252]	valid_0's binary_logloss: 0.291764
[1253]	valid_0's binary_logloss: 0.291763
[1254]	valid_0's binary_logloss: 0.291754
[1255]	valid_0's binary_logloss: 0.29175
[1256]	valid_0's binary_logloss: 0.291696
[1257]	valid_0's binary_logloss: 0.291724
[1258]	valid_0's binary_logloss: 0.291723
[1259]	valid_0's binary_logloss: 0.291744
[1260]	valid_0's binary_logloss: 0.291714
[1261]	valid_0's binary_logloss: 0.291705
[1262]	valid_0's binary_logloss: 0.291691
[1263]	valid_0's binary_logloss: 0.291702
[1264]	valid_0's binary_logloss: 0.291723
[1265]	valid_0's binary_logloss: 0.291725
[1266]	valid_0's binary_logloss: 0.291701
[1267]	valid_0's binary_logloss: 0.291718
[1268]	valid_0's binary_logloss: 0.291731
[1269]	valid_0's binary_logloss: 0.291728
[1270]	valid_0's binary_logloss: 0.291718
[1271]	valid_0's binary_logloss: 0.291703
[1272]	valid_0's binary_logloss: 0.291711
[1273]	valid_0's binary_logloss: 0.291711
[1274]	valid_0's binary_logloss: 0.

[1472]	valid_0's binary_logloss: 0.286293
[1473]	valid_0's binary_logloss: 0.286299
[1474]	valid_0's binary_logloss: 0.286294
[1475]	valid_0's binary_logloss: 0.286297
[1476]	valid_0's binary_logloss: 0.28628
[1477]	valid_0's binary_logloss: 0.286299
[1478]	valid_0's binary_logloss: 0.286289
[1479]	valid_0's binary_logloss: 0.286328
[1480]	valid_0's binary_logloss: 0.286331
[1481]	valid_0's binary_logloss: 0.286331
[1482]	valid_0's binary_logloss: 0.286338
[1483]	valid_0's binary_logloss: 0.286219
[1484]	valid_0's binary_logloss: 0.286225
[1485]	valid_0's binary_logloss: 0.286222
[1486]	valid_0's binary_logloss: 0.286247
[1487]	valid_0's binary_logloss: 0.286255
[1488]	valid_0's binary_logloss: 0.286273
[1489]	valid_0's binary_logloss: 0.286247
[1490]	valid_0's binary_logloss: 0.28622
[1491]	valid_0's binary_logloss: 0.286192
[1492]	valid_0's binary_logloss: 0.286187
[1493]	valid_0's binary_logloss: 0.286219
[1494]	valid_0's binary_logloss: 0.28623
[1495]	valid_0's binary_logloss: 0.28

In [16]:
lgbm_wrapper = LGBMClassifier(n_estimators=3200,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[209]	valid_0's binary_logloss: 0.347736
[210]	valid_0's binary_logloss: 0.347509
[211]	valid_0's binary_logloss: 0.347463
[212]	valid_0's binary_logloss: 0.347234
[213]	valid_0's binary_logloss: 0.34722
[214]	valid_0's binary_logloss: 0.347206
[215]	valid_0's binary_logloss: 0.347188
[216]	valid_0's binary_logloss: 0.346953
[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's bi

[413]	valid_0's binary_logloss: 0.32243
[414]	valid_0's binary_logloss: 0.322228
[415]	valid_0's binary_logloss: 0.322037
[416]	valid_0's binary_logloss: 0.322036
[417]	valid_0's binary_logloss: 0.321957
[418]	valid_0's binary_logloss: 0.321848
[419]	valid_0's binary_logloss: 0.321622
[420]	valid_0's binary_logloss: 0.32162
[421]	valid_0's binary_logloss: 0.321616
[422]	valid_0's binary_logloss: 0.321623
[423]	valid_0's binary_logloss: 0.321591
[424]	valid_0's binary_logloss: 0.321599
[425]	valid_0's binary_logloss: 0.321356
[426]	valid_0's binary_logloss: 0.321213
[427]	valid_0's binary_logloss: 0.320967
[428]	valid_0's binary_logloss: 0.32078
[429]	valid_0's binary_logloss: 0.32081
[430]	valid_0's binary_logloss: 0.320775
[431]	valid_0's binary_logloss: 0.320763
[432]	valid_0's binary_logloss: 0.320721
[433]	valid_0's binary_logloss: 0.320712
[434]	valid_0's binary_logloss: 0.32052
[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binar

[625]	valid_0's binary_logloss: 0.308154
[626]	valid_0's binary_logloss: 0.308127
[627]	valid_0's binary_logloss: 0.308101
[628]	valid_0's binary_logloss: 0.30812
[629]	valid_0's binary_logloss: 0.308098
[630]	valid_0's binary_logloss: 0.308107
[631]	valid_0's binary_logloss: 0.308099
[632]	valid_0's binary_logloss: 0.308108
[633]	valid_0's binary_logloss: 0.308122
[634]	valid_0's binary_logloss: 0.307943
[635]	valid_0's binary_logloss: 0.30794
[636]	valid_0's binary_logloss: 0.307838
[637]	valid_0's binary_logloss: 0.307805
[638]	valid_0's binary_logloss: 0.307797
[639]	valid_0's binary_logloss: 0.307798
[640]	valid_0's binary_logloss: 0.307776
[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's bina

...

[1442]	valid_0's binary_logloss: 0.286791
[1443]	valid_0's binary_logloss: 0.286777
[1444]	valid_0's binary_logloss: 0.286781
[1445]	valid_0's binary_logloss: 0.286756
[1446]	valid_0's binary_logloss: 0.286777
[1447]	valid_0's binary_logloss: 0.28679
[1448]	valid_0's binary_logloss: 0.286685
[1449]	valid_0's binary_logloss: 0.286689
[1450]	valid_0's binary_logloss: 0.286694
[1451]	valid_0's binary_logloss: 0.28669
[1452]	valid_0's binary_logloss: 0.286719
[1453]	valid_0's binary_logloss: 0.286724
[1454]	valid_0's binary_logloss: 0.286713
[1455]	valid_0's binary_logloss: 0.286715
[1456]	valid_0's binary_logloss: 0.286724
[1457]	valid_0's binary_logloss: 0.286566
[1458]	valid_0's binary_logloss: 0.286422
[1459]	valid_0's binary_logloss: 0.286429
[1460]	valid_0's binary_logloss: 0.286424
[1461]	valid_0's binary_logloss: 0.286375
[1462]	valid_0's binary_logloss: 0.286375
[1463]	valid_0's binary_logloss: 0.286375
[1464]	valid_0's binary_logloss: 0.286395
[1465]	valid_0's binary_logloss: 0.2

[1641]	valid_0's binary_logloss: 0.283626
[1642]	valid_0's binary_logloss: 0.283642
[1643]	valid_0's binary_logloss: 0.283661
[1644]	valid_0's binary_logloss: 0.283687
[1645]	valid_0's binary_logloss: 0.283689
[1646]	valid_0's binary_logloss: 0.283709
[1647]	valid_0's binary_logloss: 0.283691
[1648]	valid_0's binary_logloss: 0.283704
[1649]	valid_0's binary_logloss: 0.283701
[1650]	valid_0's binary_logloss: 0.283723
[1651]	valid_0's binary_logloss: 0.283747
[1652]	valid_0's binary_logloss: 0.283702
[1653]	valid_0's binary_logloss: 0.283681
[1654]	valid_0's binary_logloss: 0.283668
[1655]	valid_0's binary_logloss: 0.283678
[1656]	valid_0's binary_logloss: 0.283685
[1657]	valid_0's binary_logloss: 0.283698
[1658]	valid_0's binary_logloss: 0.283702
[1659]	valid_0's binary_logloss: 0.283697
[1660]	valid_0's binary_logloss: 0.283695
[1661]	valid_0's binary_logloss: 0.283718
[1662]	valid_0's binary_logloss: 0.283704
[1663]	valid_0's binary_logloss: 0.283719
[1664]	valid_0's binary_logloss: 0

[1858]	valid_0's binary_logloss: 0.282379
[1859]	valid_0's binary_logloss: 0.282389
[1860]	valid_0's binary_logloss: 0.282359
[1861]	valid_0's binary_logloss: 0.28237
[1862]	valid_0's binary_logloss: 0.282362
[1863]	valid_0's binary_logloss: 0.282339
[1864]	valid_0's binary_logloss: 0.282354
[1865]	valid_0's binary_logloss: 0.282363
[1866]	valid_0's binary_logloss: 0.282251
[1867]	valid_0's binary_logloss: 0.282247
[1868]	valid_0's binary_logloss: 0.282251
[1869]	valid_0's binary_logloss: 0.282288
[1870]	valid_0's binary_logloss: 0.282285
[1871]	valid_0's binary_logloss: 0.28229
[1872]	valid_0's binary_logloss: 0.282305
[1873]	valid_0's binary_logloss: 0.282309
[1874]	valid_0's binary_logloss: 0.282322
[1875]	valid_0's binary_logloss: 0.282319
[1876]	valid_0's binary_logloss: 0.282333
[1877]	valid_0's binary_logloss: 0.282175
[1878]	valid_0's binary_logloss: 0.282172
[1879]	valid_0's binary_logloss: 0.282068
[1880]	valid_0's binary_logloss: 0.282071
[1881]	valid_0's binary_logloss: 0.2

[2078]	valid_0's binary_logloss: 0.279959
[2079]	valid_0's binary_logloss: 0.279953
[2080]	valid_0's binary_logloss: 0.279932
[2081]	valid_0's binary_logloss: 0.279941
[2082]	valid_0's binary_logloss: 0.279977
[2083]	valid_0's binary_logloss: 0.280007
[2084]	valid_0's binary_logloss: 0.280021
[2085]	valid_0's binary_logloss: 0.280021
[2086]	valid_0's binary_logloss: 0.280025
[2087]	valid_0's binary_logloss: 0.280024
[2088]	valid_0's binary_logloss: 0.280019
[2089]	valid_0's binary_logloss: 0.280011
[2090]	valid_0's binary_logloss: 0.280019
[2091]	valid_0's binary_logloss: 0.280033
[2092]	valid_0's binary_logloss: 0.280045
[2093]	valid_0's binary_logloss: 0.280043
[2094]	valid_0's binary_logloss: 0.280024
[2095]	valid_0's binary_logloss: 0.280039
[2096]	valid_0's binary_logloss: 0.280045
[2097]	valid_0's binary_logloss: 0.280061
[2098]	valid_0's binary_logloss: 0.279951
[2099]	valid_0's binary_logloss: 0.279947
[2100]	valid_0's binary_logloss: 0.279894
[2101]	valid_0's binary_logloss: 0

[2294]	valid_0's binary_logloss: 0.279439
[2295]	valid_0's binary_logloss: 0.279445
[2296]	valid_0's binary_logloss: 0.279446
[2297]	valid_0's binary_logloss: 0.279452
[2298]	valid_0's binary_logloss: 0.279441
[2299]	valid_0's binary_logloss: 0.279451
[2300]	valid_0's binary_logloss: 0.279451
[2301]	valid_0's binary_logloss: 0.279467
[2302]	valid_0's binary_logloss: 0.279461
[2303]	valid_0's binary_logloss: 0.279485
[2304]	valid_0's binary_logloss: 0.279504
[2305]	valid_0's binary_logloss: 0.279474
[2306]	valid_0's binary_logloss: 0.279493
[2307]	valid_0's binary_logloss: 0.279507
오차 행렬
[[52992  1783]
 [ 6300  7667]]
정확도: 0.8824, 정밀도: 0.8113, 재현율: 0.5489,    F1: 0.6548, AUC:0.9183


In [17]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=256,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[215]	valid_0's binary_logloss: 0.347188
[216]	valid_0's binary_logloss: 0.346953
[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's binary_logloss: 0.342194
[234]	valid_0's binary_logloss: 0.341976
[235]	valid_0's binary_logloss: 0.341697
[236]	valid_0's binary_logloss: 0.341234
[237]	valid_0's binary_logloss: 0.341206
[238]	valid_0's binary_logloss: 0.341152
[239]	valid_0's b

[425]	valid_0's binary_logloss: 0.321356
[426]	valid_0's binary_logloss: 0.321213
[427]	valid_0's binary_logloss: 0.320967
[428]	valid_0's binary_logloss: 0.32078
[429]	valid_0's binary_logloss: 0.32081
[430]	valid_0's binary_logloss: 0.320775
[431]	valid_0's binary_logloss: 0.320763
[432]	valid_0's binary_logloss: 0.320721
[433]	valid_0's binary_logloss: 0.320712
[434]	valid_0's binary_logloss: 0.32052
[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binary_logloss: 0.320492
[438]	valid_0's binary_logloss: 0.320435
[439]	valid_0's binary_logloss: 0.320437
[440]	valid_0's binary_logloss: 0.320403
[441]	valid_0's binary_logloss: 0.320275
[442]	valid_0's binary_logloss: 0.320276
[443]	valid_0's binary_logloss: 0.320231
[444]	valid_0's binary_logloss: 0.320142
[445]	valid_0's binary_logloss: 0.320124
[446]	valid_0's binary_logloss: 0.320138
[447]	valid_0's binary_logloss: 0.31984
[448]	valid_0's binary_logloss: 0.319772
[449]	valid_0's bina

[635]	valid_0's binary_logloss: 0.30794
[636]	valid_0's binary_logloss: 0.307838
[637]	valid_0's binary_logloss: 0.307805
[638]	valid_0's binary_logloss: 0.307797
[639]	valid_0's binary_logloss: 0.307798
[640]	valid_0's binary_logloss: 0.307776
[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's binary_logloss: 0.307378
[650]	valid_0's binary_logloss: 0.307251
[651]	valid_0's binary_logloss: 0.30716
[652]	valid_0's binary_logloss: 0.307154
[653]	valid_0's binary_logloss: 0.307141
[654]	valid_0's binary_logloss: 0.307073
[655]	valid_0's binary_logloss: 0.307
[656]	valid_0's binary_logloss: 0.306996
[657]	valid_0's binary_logloss: 0.306976
[658]	valid_0's binary_logloss: 0.306941
[659]	valid_0's binary_

[837]	valid_0's binary_logloss: 0.30045
[838]	valid_0's binary_logloss: 0.30044
[839]	valid_0's binary_logloss: 0.300335
[840]	valid_0's binary_logloss: 0.300313
[841]	valid_0's binary_logloss: 0.30033
[842]	valid_0's binary_logloss: 0.300335
[843]	valid_0's binary_logloss: 0.300339
[844]	valid_0's binary_logloss: 0.300228
[845]	valid_0's binary_logloss: 0.300209
[846]	valid_0's binary_logloss: 0.300225
[847]	valid_0's binary_logloss: 0.300237
[848]	valid_0's binary_logloss: 0.299943
[849]	valid_0's binary_logloss: 0.29995
[850]	valid_0's binary_logloss: 0.299968
[851]	valid_0's binary_logloss: 0.299974
[852]	valid_0's binary_logloss: 0.299934
[853]	valid_0's binary_logloss: 0.299931
[854]	valid_0's binary_logloss: 0.299964
[855]	valid_0's binary_logloss: 0.299972
[856]	valid_0's binary_logloss: 0.299687
[857]	valid_0's binary_logloss: 0.299698
[858]	valid_0's binary_logloss: 0.299711
[859]	valid_0's binary_logloss: 0.299721
[860]	valid_0's binary_logloss: 0.29972
[861]	valid_0's binar

[1051]	valid_0's binary_logloss: 0.294754
[1052]	valid_0's binary_logloss: 0.29475
[1053]	valid_0's binary_logloss: 0.294763
[1054]	valid_0's binary_logloss: 0.294733
[1055]	valid_0's binary_logloss: 0.294729
[1056]	valid_0's binary_logloss: 0.294748
[1057]	valid_0's binary_logloss: 0.294711
[1058]	valid_0's binary_logloss: 0.294648
[1059]	valid_0's binary_logloss: 0.294646
[1060]	valid_0's binary_logloss: 0.294631
[1061]	valid_0's binary_logloss: 0.294635
[1062]	valid_0's binary_logloss: 0.294625
[1063]	valid_0's binary_logloss: 0.294478
[1064]	valid_0's binary_logloss: 0.294379
[1065]	valid_0's binary_logloss: 0.294359
[1066]	valid_0's binary_logloss: 0.294355
[1067]	valid_0's binary_logloss: 0.294378
[1068]	valid_0's binary_logloss: 0.29438
[1069]	valid_0's binary_logloss: 0.294378
[1070]	valid_0's binary_logloss: 0.294331
[1071]	valid_0's binary_logloss: 0.294356
[1072]	valid_0's binary_logloss: 0.294286
[1073]	valid_0's binary_logloss: 0.294291
[1074]	valid_0's binary_logloss: 0.2

[1256]	valid_0's binary_logloss: 0.291696
[1257]	valid_0's binary_logloss: 0.291724
[1258]	valid_0's binary_logloss: 0.291723
[1259]	valid_0's binary_logloss: 0.291744
[1260]	valid_0's binary_logloss: 0.291714
[1261]	valid_0's binary_logloss: 0.291705
[1262]	valid_0's binary_logloss: 0.291691
[1263]	valid_0's binary_logloss: 0.291702
[1264]	valid_0's binary_logloss: 0.291723
[1265]	valid_0's binary_logloss: 0.291725
[1266]	valid_0's binary_logloss: 0.291701
[1267]	valid_0's binary_logloss: 0.291718
[1268]	valid_0's binary_logloss: 0.291731
[1269]	valid_0's binary_logloss: 0.291728
[1270]	valid_0's binary_logloss: 0.291718
[1271]	valid_0's binary_logloss: 0.291703
[1272]	valid_0's binary_logloss: 0.291711
[1273]	valid_0's binary_logloss: 0.291711
[1274]	valid_0's binary_logloss: 0.291679
[1275]	valid_0's binary_logloss: 0.291678
[1276]	valid_0's binary_logloss: 0.291674
[1277]	valid_0's binary_logloss: 0.291671
[1278]	valid_0's binary_logloss: 0.291653
[1279]	valid_0's binary_logloss: 0

[1457]	valid_0's binary_logloss: 0.286566
[1458]	valid_0's binary_logloss: 0.286422
[1459]	valid_0's binary_logloss: 0.286429
[1460]	valid_0's binary_logloss: 0.286424
[1461]	valid_0's binary_logloss: 0.286375
[1462]	valid_0's binary_logloss: 0.286375
[1463]	valid_0's binary_logloss: 0.286375
[1464]	valid_0's binary_logloss: 0.286395
[1465]	valid_0's binary_logloss: 0.28639
[1466]	valid_0's binary_logloss: 0.286368
[1467]	valid_0's binary_logloss: 0.286395
[1468]	valid_0's binary_logloss: 0.286392
[1469]	valid_0's binary_logloss: 0.286403
[1470]	valid_0's binary_logloss: 0.286402
[1471]	valid_0's binary_logloss: 0.286347
[1472]	valid_0's binary_logloss: 0.286293
[1473]	valid_0's binary_logloss: 0.286299
[1474]	valid_0's binary_logloss: 0.286294
[1475]	valid_0's binary_logloss: 0.286297
[1476]	valid_0's binary_logloss: 0.28628
[1477]	valid_0's binary_logloss: 0.286299
[1478]	valid_0's binary_logloss: 0.286289
[1479]	valid_0's binary_logloss: 0.286328
[1480]	valid_0's binary_logloss: 0.2

In [18]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[207]	valid_0's binary_logloss: 0.348383
[208]	valid_0's binary_logloss: 0.347881
[209]	valid_0's binary_logloss: 0.347736
[210]	valid_0's binary_logloss: 0.347509
[211]	valid_0's binary_logloss: 0.347463
[212]	valid_0's binary_logloss: 0.347234
[213]	valid_0's binary_logloss: 0.34722
[214]	valid_0's binary_logloss: 0.347206
[215]	valid_0's binary_logloss: 0.347188
[216]	valid_0's binary_logloss: 0.346953
[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's bi

[414]	valid_0's binary_logloss: 0.322228
[415]	valid_0's binary_logloss: 0.322037
[416]	valid_0's binary_logloss: 0.322036
[417]	valid_0's binary_logloss: 0.321957
[418]	valid_0's binary_logloss: 0.321848
[419]	valid_0's binary_logloss: 0.321622
[420]	valid_0's binary_logloss: 0.32162
[421]	valid_0's binary_logloss: 0.321616
[422]	valid_0's binary_logloss: 0.321623
[423]	valid_0's binary_logloss: 0.321591
[424]	valid_0's binary_logloss: 0.321599
[425]	valid_0's binary_logloss: 0.321356
[426]	valid_0's binary_logloss: 0.321213
[427]	valid_0's binary_logloss: 0.320967
[428]	valid_0's binary_logloss: 0.32078
[429]	valid_0's binary_logloss: 0.32081
[430]	valid_0's binary_logloss: 0.320775
[431]	valid_0's binary_logloss: 0.320763
[432]	valid_0's binary_logloss: 0.320721
[433]	valid_0's binary_logloss: 0.320712
[434]	valid_0's binary_logloss: 0.32052
[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binary_logloss: 0.320492
[438]	valid_0's bina

[637]	valid_0's binary_logloss: 0.307805
[638]	valid_0's binary_logloss: 0.307797
[639]	valid_0's binary_logloss: 0.307798
[640]	valid_0's binary_logloss: 0.307776
[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's binary_logloss: 0.307378
[650]	valid_0's binary_logloss: 0.307251
[651]	valid_0's binary_logloss: 0.30716
[652]	valid_0's binary_logloss: 0.307154
[653]	valid_0's binary_logloss: 0.307141
[654]	valid_0's binary_logloss: 0.307073
[655]	valid_0's binary_logloss: 0.307
[656]	valid_0's binary_logloss: 0.306996
[657]	valid_0's binary_logloss: 0.306976
[658]	valid_0's binary_logloss: 0.306941
[659]	valid_0's binary_logloss: 0.306941
[660]	valid_0's binary_logloss: 0.306835
[661]	valid_0's binary

[843]	valid_0's binary_logloss: 0.300339
[844]	valid_0's binary_logloss: 0.300228
[845]	valid_0's binary_logloss: 0.300209
[846]	valid_0's binary_logloss: 0.300225
[847]	valid_0's binary_logloss: 0.300237
[848]	valid_0's binary_logloss: 0.299943
[849]	valid_0's binary_logloss: 0.29995
[850]	valid_0's binary_logloss: 0.299968
[851]	valid_0's binary_logloss: 0.299974
[852]	valid_0's binary_logloss: 0.299934
[853]	valid_0's binary_logloss: 0.299931
[854]	valid_0's binary_logloss: 0.299964
[855]	valid_0's binary_logloss: 0.299972
[856]	valid_0's binary_logloss: 0.299687
[857]	valid_0's binary_logloss: 0.299698
[858]	valid_0's binary_logloss: 0.299711
[859]	valid_0's binary_logloss: 0.299721
[860]	valid_0's binary_logloss: 0.29972
[861]	valid_0's binary_logloss: 0.299728
[862]	valid_0's binary_logloss: 0.299743
[863]	valid_0's binary_logloss: 0.299676
[864]	valid_0's binary_logloss: 0.299567
[865]	valid_0's binary_logloss: 0.299563
[866]	valid_0's binary_logloss: 0.299554
[867]	valid_0's bi

[1069]	valid_0's binary_logloss: 0.294378
[1070]	valid_0's binary_logloss: 0.294331
[1071]	valid_0's binary_logloss: 0.294356
[1072]	valid_0's binary_logloss: 0.294286
[1073]	valid_0's binary_logloss: 0.294291
[1074]	valid_0's binary_logloss: 0.294313
[1075]	valid_0's binary_logloss: 0.294328
[1076]	valid_0's binary_logloss: 0.294286
[1077]	valid_0's binary_logloss: 0.294286
[1078]	valid_0's binary_logloss: 0.294304
[1079]	valid_0's binary_logloss: 0.294146
[1080]	valid_0's binary_logloss: 0.294163
[1081]	valid_0's binary_logloss: 0.294157
[1082]	valid_0's binary_logloss: 0.294157
[1083]	valid_0's binary_logloss: 0.293996
[1084]	valid_0's binary_logloss: 0.294002
[1085]	valid_0's binary_logloss: 0.293985
[1086]	valid_0's binary_logloss: 0.294015
[1087]	valid_0's binary_logloss: 0.294008
[1088]	valid_0's binary_logloss: 0.293979
[1089]	valid_0's binary_logloss: 0.293991
[1090]	valid_0's binary_logloss: 0.294002
[1091]	valid_0's binary_logloss: 0.293991
[1092]	valid_0's binary_logloss: 0

[1266]	valid_0's binary_logloss: 0.291701
[1267]	valid_0's binary_logloss: 0.291718
[1268]	valid_0's binary_logloss: 0.291731
[1269]	valid_0's binary_logloss: 0.291728
[1270]	valid_0's binary_logloss: 0.291718
[1271]	valid_0's binary_logloss: 0.291703
[1272]	valid_0's binary_logloss: 0.291711
[1273]	valid_0's binary_logloss: 0.291711
[1274]	valid_0's binary_logloss: 0.291679
[1275]	valid_0's binary_logloss: 0.291678
[1276]	valid_0's binary_logloss: 0.291674
[1277]	valid_0's binary_logloss: 0.291671
[1278]	valid_0's binary_logloss: 0.291653
[1279]	valid_0's binary_logloss: 0.291646
[1280]	valid_0's binary_logloss: 0.291645
[1281]	valid_0's binary_logloss: 0.291639
[1282]	valid_0's binary_logloss: 0.291622
[1283]	valid_0's binary_logloss: 0.291638
[1284]	valid_0's binary_logloss: 0.291523
[1285]	valid_0's binary_logloss: 0.291494
[1286]	valid_0's binary_logloss: 0.29151
[1287]	valid_0's binary_logloss: 0.29148
[1288]	valid_0's binary_logloss: 0.291435
[1289]	valid_0's binary_logloss: 0.2

[1481]	valid_0's binary_logloss: 0.286331
[1482]	valid_0's binary_logloss: 0.286338
[1483]	valid_0's binary_logloss: 0.286219
[1484]	valid_0's binary_logloss: 0.286225
[1485]	valid_0's binary_logloss: 0.286222
[1486]	valid_0's binary_logloss: 0.286247
[1487]	valid_0's binary_logloss: 0.286255
[1488]	valid_0's binary_logloss: 0.286273
[1489]	valid_0's binary_logloss: 0.286247
[1490]	valid_0's binary_logloss: 0.28622
[1491]	valid_0's binary_logloss: 0.286192
[1492]	valid_0's binary_logloss: 0.286187
[1493]	valid_0's binary_logloss: 0.286219
[1494]	valid_0's binary_logloss: 0.28623
[1495]	valid_0's binary_logloss: 0.286206
[1496]	valid_0's binary_logloss: 0.286043
[1497]	valid_0's binary_logloss: 0.286008
[1498]	valid_0's binary_logloss: 0.286016
[1499]	valid_0's binary_logloss: 0.286018
[1500]	valid_0's binary_logloss: 0.285998
[1501]	valid_0's binary_logloss: 0.286012
[1502]	valid_0's binary_logloss: 0.286036
[1503]	valid_0's binary_logloss: 0.286035
[1504]	valid_0's binary_logloss: 0.2

In [19]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491456
[2]	valid_0's binary_logloss: 0.482132
[3]	valid_0's binary_logloss: 0.474581
[4]	valid_0's binary_logloss: 0.468289
[5]	valid_0's binary_logloss: 0.463124
[6]	valid_0's binary_logloss: 0.458696
[7]	valid_0's binary_logloss: 0.454779
[8]	valid_0's binary_logloss: 0.451463
[9]	valid_0's binary_logloss: 0.448443
[10]	valid_0's binary_logloss: 0.445825
[11]	valid_0's binary_logloss: 0.443488
[12]	valid_0's binary_logloss: 0.441303
[13]	valid_0's binary_logloss: 0.439404
[14]	valid_0's binary_logloss: 0.437318
[15]	valid_0's binary_logloss: 0.435587
[16]	valid_0's binary_logloss: 0.433968
[17]	valid_0's binary_logloss: 0.432517
[18]	valid_0's binary_logloss: 0.430551
[19]	valid_0's binary_logloss: 0.429124
[20]	valid_0's binary_logloss: 0.427743
[21]	valid_0's binary_logloss: 0.426467
[22]	valid_0's binary_logloss: 0.425438
[23]	valid_0's binary_logloss: 0.424321
[24]	valid_0's binary_logloss: 0.423273
[25]	valid_0's binary_logloss: 0.4216
[26]	valid_

[217]	valid_0's binary_logloss: 0.346911
[218]	valid_0's binary_logloss: 0.346434
[219]	valid_0's binary_logloss: 0.345813
[220]	valid_0's binary_logloss: 0.345212
[221]	valid_0's binary_logloss: 0.345168
[222]	valid_0's binary_logloss: 0.345074
[223]	valid_0's binary_logloss: 0.344259
[224]	valid_0's binary_logloss: 0.344067
[225]	valid_0's binary_logloss: 0.34393
[226]	valid_0's binary_logloss: 0.343737
[227]	valid_0's binary_logloss: 0.343405
[228]	valid_0's binary_logloss: 0.343379
[229]	valid_0's binary_logloss: 0.342975
[230]	valid_0's binary_logloss: 0.342714
[231]	valid_0's binary_logloss: 0.342673
[232]	valid_0's binary_logloss: 0.342259
[233]	valid_0's binary_logloss: 0.342194
[234]	valid_0's binary_logloss: 0.341976
[235]	valid_0's binary_logloss: 0.341697
[236]	valid_0's binary_logloss: 0.341234
[237]	valid_0's binary_logloss: 0.341206
[238]	valid_0's binary_logloss: 0.341152
[239]	valid_0's binary_logloss: 0.341113
[240]	valid_0's binary_logloss: 0.340959
[241]	valid_0's b

[430]	valid_0's binary_logloss: 0.320775
[431]	valid_0's binary_logloss: 0.320763
[432]	valid_0's binary_logloss: 0.320721
[433]	valid_0's binary_logloss: 0.320712
[434]	valid_0's binary_logloss: 0.32052
[435]	valid_0's binary_logloss: 0.320485
[436]	valid_0's binary_logloss: 0.320484
[437]	valid_0's binary_logloss: 0.320492
[438]	valid_0's binary_logloss: 0.320435
[439]	valid_0's binary_logloss: 0.320437
[440]	valid_0's binary_logloss: 0.320403
[441]	valid_0's binary_logloss: 0.320275
[442]	valid_0's binary_logloss: 0.320276
[443]	valid_0's binary_logloss: 0.320231
[444]	valid_0's binary_logloss: 0.320142
[445]	valid_0's binary_logloss: 0.320124
[446]	valid_0's binary_logloss: 0.320138
[447]	valid_0's binary_logloss: 0.31984
[448]	valid_0's binary_logloss: 0.319772
[449]	valid_0's binary_logloss: 0.319567
[450]	valid_0's binary_logloss: 0.319456
[451]	valid_0's binary_logloss: 0.319465
[452]	valid_0's binary_logloss: 0.3194
[453]	valid_0's binary_logloss: 0.319373
[454]	valid_0's bina

[639]	valid_0's binary_logloss: 0.307798
[640]	valid_0's binary_logloss: 0.307776
[641]	valid_0's binary_logloss: 0.307801
[642]	valid_0's binary_logloss: 0.307819
[643]	valid_0's binary_logloss: 0.307783
[644]	valid_0's binary_logloss: 0.30773
[645]	valid_0's binary_logloss: 0.30765
[646]	valid_0's binary_logloss: 0.307443
[647]	valid_0's binary_logloss: 0.307442
[648]	valid_0's binary_logloss: 0.307366
[649]	valid_0's binary_logloss: 0.307378
[650]	valid_0's binary_logloss: 0.307251
[651]	valid_0's binary_logloss: 0.30716
[652]	valid_0's binary_logloss: 0.307154
[653]	valid_0's binary_logloss: 0.307141
[654]	valid_0's binary_logloss: 0.307073
[655]	valid_0's binary_logloss: 0.307
[656]	valid_0's binary_logloss: 0.306996
[657]	valid_0's binary_logloss: 0.306976
[658]	valid_0's binary_logloss: 0.306941
[659]	valid_0's binary_logloss: 0.306941
[660]	valid_0's binary_logloss: 0.306835
[661]	valid_0's binary_logloss: 0.306767
[662]	valid_0's binary_logloss: 0.306707
[663]	valid_0's binary

[847]	valid_0's binary_logloss: 0.300237
[848]	valid_0's binary_logloss: 0.299943
[849]	valid_0's binary_logloss: 0.29995
[850]	valid_0's binary_logloss: 0.299968
[851]	valid_0's binary_logloss: 0.299974
[852]	valid_0's binary_logloss: 0.299934
[853]	valid_0's binary_logloss: 0.299931
[854]	valid_0's binary_logloss: 0.299964
[855]	valid_0's binary_logloss: 0.299972
[856]	valid_0's binary_logloss: 0.299687
[857]	valid_0's binary_logloss: 0.299698
[858]	valid_0's binary_logloss: 0.299711
[859]	valid_0's binary_logloss: 0.299721
[860]	valid_0's binary_logloss: 0.29972
[861]	valid_0's binary_logloss: 0.299728
[862]	valid_0's binary_logloss: 0.299743
[863]	valid_0's binary_logloss: 0.299676
[864]	valid_0's binary_logloss: 0.299567
[865]	valid_0's binary_logloss: 0.299563
[866]	valid_0's binary_logloss: 0.299554
[867]	valid_0's binary_logloss: 0.299568
[868]	valid_0's binary_logloss: 0.299559
[869]	valid_0's binary_logloss: 0.299533
[870]	valid_0's binary_logloss: 0.299539
[871]	valid_0's bi

[1054]	valid_0's binary_logloss: 0.294733
[1055]	valid_0's binary_logloss: 0.294729
[1056]	valid_0's binary_logloss: 0.294748
[1057]	valid_0's binary_logloss: 0.294711
[1058]	valid_0's binary_logloss: 0.294648
[1059]	valid_0's binary_logloss: 0.294646
[1060]	valid_0's binary_logloss: 0.294631
[1061]	valid_0's binary_logloss: 0.294635
[1062]	valid_0's binary_logloss: 0.294625
[1063]	valid_0's binary_logloss: 0.294478
[1064]	valid_0's binary_logloss: 0.294379
[1065]	valid_0's binary_logloss: 0.294359
[1066]	valid_0's binary_logloss: 0.294355
[1067]	valid_0's binary_logloss: 0.294378
[1068]	valid_0's binary_logloss: 0.29438
[1069]	valid_0's binary_logloss: 0.294378
[1070]	valid_0's binary_logloss: 0.294331
[1071]	valid_0's binary_logloss: 0.294356
[1072]	valid_0's binary_logloss: 0.294286
[1073]	valid_0's binary_logloss: 0.294291
[1074]	valid_0's binary_logloss: 0.294313
[1075]	valid_0's binary_logloss: 0.294328
[1076]	valid_0's binary_logloss: 0.294286
[1077]	valid_0's binary_logloss: 0.

[1262]	valid_0's binary_logloss: 0.291691
[1263]	valid_0's binary_logloss: 0.291702
[1264]	valid_0's binary_logloss: 0.291723
[1265]	valid_0's binary_logloss: 0.291725
[1266]	valid_0's binary_logloss: 0.291701
[1267]	valid_0's binary_logloss: 0.291718
[1268]	valid_0's binary_logloss: 0.291731
[1269]	valid_0's binary_logloss: 0.291728
[1270]	valid_0's binary_logloss: 0.291718
[1271]	valid_0's binary_logloss: 0.291703
[1272]	valid_0's binary_logloss: 0.291711
[1273]	valid_0's binary_logloss: 0.291711
[1274]	valid_0's binary_logloss: 0.291679
[1275]	valid_0's binary_logloss: 0.291678
[1276]	valid_0's binary_logloss: 0.291674
[1277]	valid_0's binary_logloss: 0.291671
[1278]	valid_0's binary_logloss: 0.291653
[1279]	valid_0's binary_logloss: 0.291646
[1280]	valid_0's binary_logloss: 0.291645
[1281]	valid_0's binary_logloss: 0.291639
[1282]	valid_0's binary_logloss: 0.291622
[1283]	valid_0's binary_logloss: 0.291638
[1284]	valid_0's binary_logloss: 0.291523
[1285]	valid_0's binary_logloss: 0

[1458]	valid_0's binary_logloss: 0.286422
[1459]	valid_0's binary_logloss: 0.286429
[1460]	valid_0's binary_logloss: 0.286424
[1461]	valid_0's binary_logloss: 0.286375
[1462]	valid_0's binary_logloss: 0.286375
[1463]	valid_0's binary_logloss: 0.286375
[1464]	valid_0's binary_logloss: 0.286395
[1465]	valid_0's binary_logloss: 0.28639
[1466]	valid_0's binary_logloss: 0.286368
[1467]	valid_0's binary_logloss: 0.286395
[1468]	valid_0's binary_logloss: 0.286392
[1469]	valid_0's binary_logloss: 0.286403
[1470]	valid_0's binary_logloss: 0.286402
[1471]	valid_0's binary_logloss: 0.286347
[1472]	valid_0's binary_logloss: 0.286293
[1473]	valid_0's binary_logloss: 0.286299
[1474]	valid_0's binary_logloss: 0.286294
[1475]	valid_0's binary_logloss: 0.286297
[1476]	valid_0's binary_logloss: 0.28628
[1477]	valid_0's binary_logloss: 0.286299
[1478]	valid_0's binary_logloss: 0.286289
[1479]	valid_0's binary_logloss: 0.286328
[1480]	valid_0's binary_logloss: 0.286331
[1481]	valid_0's binary_logloss: 0.2

In [23]:
lgbm_wrapper = LGBMClassifier(n_estimators=1400,max_depth=128,min_child_samples=80,num_leaves=81,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491443
[2]	valid_0's binary_logloss: 0.482125
[3]	valid_0's binary_logloss: 0.474591
[4]	valid_0's binary_logloss: 0.468281
[5]	valid_0's binary_logloss: 0.46306
[6]	valid_0's binary_logloss: 0.458616
[7]	valid_0's binary_logloss: 0.454651
[8]	valid_0's binary_logloss: 0.451346
[9]	valid_0's binary_logloss: 0.448519
[10]	valid_0's binary_logloss: 0.445835
[11]	valid_0's binary_logloss: 0.443381
[12]	valid_0's binary_logloss: 0.441237
[13]	valid_0's binary_logloss: 0.439308
[14]	valid_0's binary_logloss: 0.437401
[15]	valid_0's binary_logloss: 0.435568
[16]	valid_0's binary_logloss: 0.43358
[17]	valid_0's binary_logloss: 0.431963
[18]	valid_0's binary_logloss: 0.430675
[19]	valid_0's binary_logloss: 0.42949
[20]	valid_0's binary_logloss: 0.42822
[21]	valid_0's binary_logloss: 0.426964
[22]	valid_0's binary_logloss: 0.425851
[23]	valid_0's binary_logloss: 0.424839
[24]	valid_0's binary_logloss: 0.423923
[25]	valid_0's binary_logloss: 0.422873
[26]	valid_0'

[220]	valid_0's binary_logloss: 0.344211
[221]	valid_0's binary_logloss: 0.344178
[222]	valid_0's binary_logloss: 0.344056
[223]	valid_0's binary_logloss: 0.343991
[224]	valid_0's binary_logloss: 0.343901
[225]	valid_0's binary_logloss: 0.343519
[226]	valid_0's binary_logloss: 0.343498
[227]	valid_0's binary_logloss: 0.343408
[228]	valid_0's binary_logloss: 0.343112
[229]	valid_0's binary_logloss: 0.342712
[230]	valid_0's binary_logloss: 0.342683
[231]	valid_0's binary_logloss: 0.342665
[232]	valid_0's binary_logloss: 0.34268
[233]	valid_0's binary_logloss: 0.342666
[234]	valid_0's binary_logloss: 0.342557
[235]	valid_0's binary_logloss: 0.342469
[236]	valid_0's binary_logloss: 0.342291
[237]	valid_0's binary_logloss: 0.342241
[238]	valid_0's binary_logloss: 0.34219
[239]	valid_0's binary_logloss: 0.342147
[240]	valid_0's binary_logloss: 0.342015
[241]	valid_0's binary_logloss: 0.341948
[242]	valid_0's binary_logloss: 0.341909
[243]	valid_0's binary_logloss: 0.34187
[244]	valid_0's bin

[425]	valid_0's binary_logloss: 0.320873
[426]	valid_0's binary_logloss: 0.320873
[427]	valid_0's binary_logloss: 0.320775
[428]	valid_0's binary_logloss: 0.320721
[429]	valid_0's binary_logloss: 0.32068
[430]	valid_0's binary_logloss: 0.320666
[431]	valid_0's binary_logloss: 0.320618
[432]	valid_0's binary_logloss: 0.320636
[433]	valid_0's binary_logloss: 0.320418
[434]	valid_0's binary_logloss: 0.320058
[435]	valid_0's binary_logloss: 0.320071
[436]	valid_0's binary_logloss: 0.31947
[437]	valid_0's binary_logloss: 0.319259
[438]	valid_0's binary_logloss: 0.319251
[439]	valid_0's binary_logloss: 0.31888
[440]	valid_0's binary_logloss: 0.31887
[441]	valid_0's binary_logloss: 0.31885
[442]	valid_0's binary_logloss: 0.318801
[443]	valid_0's binary_logloss: 0.318757
[444]	valid_0's binary_logloss: 0.31871
[445]	valid_0's binary_logloss: 0.318733
[446]	valid_0's binary_logloss: 0.318736
[447]	valid_0's binary_logloss: 0.318735
[448]	valid_0's binary_logloss: 0.318694
[449]	valid_0's binary

[628]	valid_0's binary_logloss: 0.308131
[629]	valid_0's binary_logloss: 0.307999
[630]	valid_0's binary_logloss: 0.30798
[631]	valid_0's binary_logloss: 0.307918
[632]	valid_0's binary_logloss: 0.307897
[633]	valid_0's binary_logloss: 0.307877
[634]	valid_0's binary_logloss: 0.307773
[635]	valid_0's binary_logloss: 0.307783
[636]	valid_0's binary_logloss: 0.307785
[637]	valid_0's binary_logloss: 0.307781
[638]	valid_0's binary_logloss: 0.307763
[639]	valid_0's binary_logloss: 0.307715
[640]	valid_0's binary_logloss: 0.307721
[641]	valid_0's binary_logloss: 0.307698
[642]	valid_0's binary_logloss: 0.307568
[643]	valid_0's binary_logloss: 0.30758
[644]	valid_0's binary_logloss: 0.307402
[645]	valid_0's binary_logloss: 0.307356
[646]	valid_0's binary_logloss: 0.30722
[647]	valid_0's binary_logloss: 0.3072
[648]	valid_0's binary_logloss: 0.307213
[649]	valid_0's binary_logloss: 0.307199
[650]	valid_0's binary_logloss: 0.307129
[651]	valid_0's binary_logloss: 0.307146
[652]	valid_0's binar

[831]	valid_0's binary_logloss: 0.301576
[832]	valid_0's binary_logloss: 0.301415
[833]	valid_0's binary_logloss: 0.301283
[834]	valid_0's binary_logloss: 0.301303
[835]	valid_0's binary_logloss: 0.301259
[836]	valid_0's binary_logloss: 0.301275
[837]	valid_0's binary_logloss: 0.301273
[838]	valid_0's binary_logloss: 0.301277
[839]	valid_0's binary_logloss: 0.301183
[840]	valid_0's binary_logloss: 0.30096
[841]	valid_0's binary_logloss: 0.300861
[842]	valid_0's binary_logloss: 0.300847
[843]	valid_0's binary_logloss: 0.300824
[844]	valid_0's binary_logloss: 0.30085
[845]	valid_0's binary_logloss: 0.300839
[846]	valid_0's binary_logloss: 0.300739
[847]	valid_0's binary_logloss: 0.300713
[848]	valid_0's binary_logloss: 0.300708
[849]	valid_0's binary_logloss: 0.300601
[850]	valid_0's binary_logloss: 0.30049
[851]	valid_0's binary_logloss: 0.300499
[852]	valid_0's binary_logloss: 0.300491
[853]	valid_0's binary_logloss: 0.300471
[854]	valid_0's binary_logloss: 0.30048
[855]	valid_0's bina

[1046]	valid_0's binary_logloss: 0.293991
[1047]	valid_0's binary_logloss: 0.293908
[1048]	valid_0's binary_logloss: 0.293928
[1049]	valid_0's binary_logloss: 0.293953
[1050]	valid_0's binary_logloss: 0.293949
[1051]	valid_0's binary_logloss: 0.293813
[1052]	valid_0's binary_logloss: 0.293819
[1053]	valid_0's binary_logloss: 0.29383
[1054]	valid_0's binary_logloss: 0.293847
[1055]	valid_0's binary_logloss: 0.293835
[1056]	valid_0's binary_logloss: 0.293844
[1057]	valid_0's binary_logloss: 0.293846
[1058]	valid_0's binary_logloss: 0.293831
[1059]	valid_0's binary_logloss: 0.29383
[1060]	valid_0's binary_logloss: 0.293837
[1061]	valid_0's binary_logloss: 0.29373
[1062]	valid_0's binary_logloss: 0.293747
[1063]	valid_0's binary_logloss: 0.293707
[1064]	valid_0's binary_logloss: 0.293734
[1065]	valid_0's binary_logloss: 0.293747
[1066]	valid_0's binary_logloss: 0.293736
[1067]	valid_0's binary_logloss: 0.29375
[1068]	valid_0's binary_logloss: 0.293573
[1069]	valid_0's binary_logloss: 0.293

[1264]	valid_0's binary_logloss: 0.28944
[1265]	valid_0's binary_logloss: 0.289442
[1266]	valid_0's binary_logloss: 0.289473
[1267]	valid_0's binary_logloss: 0.289476
[1268]	valid_0's binary_logloss: 0.289466
[1269]	valid_0's binary_logloss: 0.289464
[1270]	valid_0's binary_logloss: 0.289423
[1271]	valid_0's binary_logloss: 0.289428
[1272]	valid_0's binary_logloss: 0.289336
[1273]	valid_0's binary_logloss: 0.289341
[1274]	valid_0's binary_logloss: 0.289364
[1275]	valid_0's binary_logloss: 0.289223
[1276]	valid_0's binary_logloss: 0.289227
[1277]	valid_0's binary_logloss: 0.28923
[1278]	valid_0's binary_logloss: 0.289193
[1279]	valid_0's binary_logloss: 0.289142
[1280]	valid_0's binary_logloss: 0.288941
[1281]	valid_0's binary_logloss: 0.28894
[1282]	valid_0's binary_logloss: 0.288892
[1283]	valid_0's binary_logloss: 0.288905
[1284]	valid_0's binary_logloss: 0.288917
[1285]	valid_0's binary_logloss: 0.288914
[1286]	valid_0's binary_logloss: 0.288825
[1287]	valid_0's binary_logloss: 0.28

In [24]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=80,num_leaves=64,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491443
[2]	valid_0's binary_logloss: 0.482125
[3]	valid_0's binary_logloss: 0.474591
[4]	valid_0's binary_logloss: 0.468281
[5]	valid_0's binary_logloss: 0.46306
[6]	valid_0's binary_logloss: 0.458616
[7]	valid_0's binary_logloss: 0.454651
[8]	valid_0's binary_logloss: 0.451346
[9]	valid_0's binary_logloss: 0.448519
[10]	valid_0's binary_logloss: 0.445835
[11]	valid_0's binary_logloss: 0.443381
[12]	valid_0's binary_logloss: 0.441237
[13]	valid_0's binary_logloss: 0.439308
[14]	valid_0's binary_logloss: 0.437401
[15]	valid_0's binary_logloss: 0.435568
[16]	valid_0's binary_logloss: 0.43358
[17]	valid_0's binary_logloss: 0.431963
[18]	valid_0's binary_logloss: 0.430675
[19]	valid_0's binary_logloss: 0.42949
[20]	valid_0's binary_logloss: 0.42822
[21]	valid_0's binary_logloss: 0.426964
[22]	valid_0's binary_logloss: 0.425851
[23]	valid_0's binary_logloss: 0.424839
[24]	valid_0's binary_logloss: 0.423923
[25]	valid_0's binary_logloss: 0.422873
[26]	valid_0'

[214]	valid_0's binary_logloss: 0.344575
[215]	valid_0's binary_logloss: 0.34459
[216]	valid_0's binary_logloss: 0.344576
[217]	valid_0's binary_logloss: 0.344538
[218]	valid_0's binary_logloss: 0.344432
[219]	valid_0's binary_logloss: 0.344418
[220]	valid_0's binary_logloss: 0.344211
[221]	valid_0's binary_logloss: 0.344178
[222]	valid_0's binary_logloss: 0.344056
[223]	valid_0's binary_logloss: 0.343991
[224]	valid_0's binary_logloss: 0.343901
[225]	valid_0's binary_logloss: 0.343519
[226]	valid_0's binary_logloss: 0.343498
[227]	valid_0's binary_logloss: 0.343408
[228]	valid_0's binary_logloss: 0.343112
[229]	valid_0's binary_logloss: 0.342712
[230]	valid_0's binary_logloss: 0.342683
[231]	valid_0's binary_logloss: 0.342665
[232]	valid_0's binary_logloss: 0.34268
[233]	valid_0's binary_logloss: 0.342666
[234]	valid_0's binary_logloss: 0.342557
[235]	valid_0's binary_logloss: 0.342469
[236]	valid_0's binary_logloss: 0.342291
[237]	valid_0's binary_logloss: 0.342241
[238]	valid_0's bi

[422]	valid_0's binary_logloss: 0.321619
[423]	valid_0's binary_logloss: 0.321195
[424]	valid_0's binary_logloss: 0.320894
[425]	valid_0's binary_logloss: 0.320873
[426]	valid_0's binary_logloss: 0.320873
[427]	valid_0's binary_logloss: 0.320775
[428]	valid_0's binary_logloss: 0.320721
[429]	valid_0's binary_logloss: 0.32068
[430]	valid_0's binary_logloss: 0.320666
[431]	valid_0's binary_logloss: 0.320618
[432]	valid_0's binary_logloss: 0.320636
[433]	valid_0's binary_logloss: 0.320418
[434]	valid_0's binary_logloss: 0.320058
[435]	valid_0's binary_logloss: 0.320071
[436]	valid_0's binary_logloss: 0.31947
[437]	valid_0's binary_logloss: 0.319259
[438]	valid_0's binary_logloss: 0.319251
[439]	valid_0's binary_logloss: 0.31888
[440]	valid_0's binary_logloss: 0.31887
[441]	valid_0's binary_logloss: 0.31885
[442]	valid_0's binary_logloss: 0.318801
[443]	valid_0's binary_logloss: 0.318757
[444]	valid_0's binary_logloss: 0.31871
[445]	valid_0's binary_logloss: 0.318733
[446]	valid_0's binary

[626]	valid_0's binary_logloss: 0.308153
[627]	valid_0's binary_logloss: 0.308145
[628]	valid_0's binary_logloss: 0.308131
[629]	valid_0's binary_logloss: 0.307999
[630]	valid_0's binary_logloss: 0.30798
[631]	valid_0's binary_logloss: 0.307918
[632]	valid_0's binary_logloss: 0.307897
[633]	valid_0's binary_logloss: 0.307877
[634]	valid_0's binary_logloss: 0.307773
[635]	valid_0's binary_logloss: 0.307783
[636]	valid_0's binary_logloss: 0.307785
[637]	valid_0's binary_logloss: 0.307781
[638]	valid_0's binary_logloss: 0.307763
[639]	valid_0's binary_logloss: 0.307715
[640]	valid_0's binary_logloss: 0.307721
[641]	valid_0's binary_logloss: 0.307698
[642]	valid_0's binary_logloss: 0.307568
[643]	valid_0's binary_logloss: 0.30758
[644]	valid_0's binary_logloss: 0.307402
[645]	valid_0's binary_logloss: 0.307356
[646]	valid_0's binary_logloss: 0.30722
[647]	valid_0's binary_logloss: 0.3072
[648]	valid_0's binary_logloss: 0.307213
[649]	valid_0's binary_logloss: 0.307199
[650]	valid_0's binar

[851]	valid_0's binary_logloss: 0.300499
[852]	valid_0's binary_logloss: 0.300491
[853]	valid_0's binary_logloss: 0.300471
[854]	valid_0's binary_logloss: 0.30048
[855]	valid_0's binary_logloss: 0.300482
[856]	valid_0's binary_logloss: 0.300512
[857]	valid_0's binary_logloss: 0.300525
[858]	valid_0's binary_logloss: 0.30054
[859]	valid_0's binary_logloss: 0.300528
[860]	valid_0's binary_logloss: 0.300547
[861]	valid_0's binary_logloss: 0.300556
[862]	valid_0's binary_logloss: 0.300569
[863]	valid_0's binary_logloss: 0.300583
[864]	valid_0's binary_logloss: 0.300565
[865]	valid_0's binary_logloss: 0.300563
[866]	valid_0's binary_logloss: 0.300561
[867]	valid_0's binary_logloss: 0.30055
[868]	valid_0's binary_logloss: 0.300531
[869]	valid_0's binary_logloss: 0.300316
[870]	valid_0's binary_logloss: 0.300106
[871]	valid_0's binary_logloss: 0.300118
[872]	valid_0's binary_logloss: 0.300136
[873]	valid_0's binary_logloss: 0.300099
[874]	valid_0's binary_logloss: 0.300112
[875]	valid_0's bin

[1068]	valid_0's binary_logloss: 0.293573
[1069]	valid_0's binary_logloss: 0.293423
[1070]	valid_0's binary_logloss: 0.293407
[1071]	valid_0's binary_logloss: 0.293337
[1072]	valid_0's binary_logloss: 0.293185
[1073]	valid_0's binary_logloss: 0.293176
[1074]	valid_0's binary_logloss: 0.293113
[1075]	valid_0's binary_logloss: 0.293092
[1076]	valid_0's binary_logloss: 0.293093
[1077]	valid_0's binary_logloss: 0.293074
[1078]	valid_0's binary_logloss: 0.293096
[1079]	valid_0's binary_logloss: 0.293094
[1080]	valid_0's binary_logloss: 0.293098
[1081]	valid_0's binary_logloss: 0.293114
[1082]	valid_0's binary_logloss: 0.293084
[1083]	valid_0's binary_logloss: 0.293073
[1084]	valid_0's binary_logloss: 0.292866
[1085]	valid_0's binary_logloss: 0.292614
[1086]	valid_0's binary_logloss: 0.29263
[1087]	valid_0's binary_logloss: 0.292652
[1088]	valid_0's binary_logloss: 0.292667
[1089]	valid_0's binary_logloss: 0.292658
[1090]	valid_0's binary_logloss: 0.29266
[1091]	valid_0's binary_logloss: 0.2

[1280]	valid_0's binary_logloss: 0.288941
[1281]	valid_0's binary_logloss: 0.28894
[1282]	valid_0's binary_logloss: 0.288892
[1283]	valid_0's binary_logloss: 0.288905
[1284]	valid_0's binary_logloss: 0.288917
[1285]	valid_0's binary_logloss: 0.288914
[1286]	valid_0's binary_logloss: 0.288825
[1287]	valid_0's binary_logloss: 0.288818
[1288]	valid_0's binary_logloss: 0.288803
[1289]	valid_0's binary_logloss: 0.288777
[1290]	valid_0's binary_logloss: 0.288779
[1291]	valid_0's binary_logloss: 0.288777
[1292]	valid_0's binary_logloss: 0.288787
[1293]	valid_0's binary_logloss: 0.288742
[1294]	valid_0's binary_logloss: 0.28875
[1295]	valid_0's binary_logloss: 0.288779
[1296]	valid_0's binary_logloss: 0.288814
[1297]	valid_0's binary_logloss: 0.288814
[1298]	valid_0's binary_logloss: 0.288823
[1299]	valid_0's binary_logloss: 0.288606
[1300]	valid_0's binary_logloss: 0.288517
[1301]	valid_0's binary_logloss: 0.288534
[1302]	valid_0's binary_logloss: 0.288557
[1303]	valid_0's binary_logloss: 0.2

[1476]	valid_0's binary_logloss: 0.286711
[1477]	valid_0's binary_logloss: 0.286706
[1478]	valid_0's binary_logloss: 0.286685
[1479]	valid_0's binary_logloss: 0.286658
[1480]	valid_0's binary_logloss: 0.286657
[1481]	valid_0's binary_logloss: 0.286671
[1482]	valid_0's binary_logloss: 0.286584
[1483]	valid_0's binary_logloss: 0.286598
[1484]	valid_0's binary_logloss: 0.286604
[1485]	valid_0's binary_logloss: 0.286542
[1486]	valid_0's binary_logloss: 0.286515
[1487]	valid_0's binary_logloss: 0.286471
[1488]	valid_0's binary_logloss: 0.286467
[1489]	valid_0's binary_logloss: 0.286456
[1490]	valid_0's binary_logloss: 0.286379
[1491]	valid_0's binary_logloss: 0.286376
[1492]	valid_0's binary_logloss: 0.286295
[1493]	valid_0's binary_logloss: 0.286299
[1494]	valid_0's binary_logloss: 0.286318
[1495]	valid_0's binary_logloss: 0.286318
[1496]	valid_0's binary_logloss: 0.286269
[1497]	valid_0's binary_logloss: 0.286289
[1498]	valid_0's binary_logloss: 0.286305
[1499]	valid_0's binary_logloss: 0

In [25]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=80,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491029
[2]	valid_0's binary_logloss: 0.481423
[3]	valid_0's binary_logloss: 0.473585
[4]	valid_0's binary_logloss: 0.467049
[5]	valid_0's binary_logloss: 0.461671
[6]	valid_0's binary_logloss: 0.456964
[7]	valid_0's binary_logloss: 0.452862
[8]	valid_0's binary_logloss: 0.449481
[9]	valid_0's binary_logloss: 0.446126
[10]	valid_0's binary_logloss: 0.443096
[11]	valid_0's binary_logloss: 0.440703
[12]	valid_0's binary_logloss: 0.438571
[13]	valid_0's binary_logloss: 0.436462
[14]	valid_0's binary_logloss: 0.434473
[15]	valid_0's binary_logloss: 0.432062
[16]	valid_0's binary_logloss: 0.430186
[17]	valid_0's binary_logloss: 0.42804
[18]	valid_0's binary_logloss: 0.426584
[19]	valid_0's binary_logloss: 0.42486
[20]	valid_0's binary_logloss: 0.423681
[21]	valid_0's binary_logloss: 0.422409
[22]	valid_0's binary_logloss: 0.420936
[23]	valid_0's binary_logloss: 0.419946
[24]	valid_0's binary_logloss: 0.418639
[25]	valid_0's binary_logloss: 0.417779
[26]	valid_

[211]	valid_0's binary_logloss: 0.337463
[212]	valid_0's binary_logloss: 0.337284
[213]	valid_0's binary_logloss: 0.336916
[214]	valid_0's binary_logloss: 0.336852
[215]	valid_0's binary_logloss: 0.336731
[216]	valid_0's binary_logloss: 0.336693
[217]	valid_0's binary_logloss: 0.336616
[218]	valid_0's binary_logloss: 0.336639
[219]	valid_0's binary_logloss: 0.336595
[220]	valid_0's binary_logloss: 0.336559
[221]	valid_0's binary_logloss: 0.336514
[222]	valid_0's binary_logloss: 0.336504
[223]	valid_0's binary_logloss: 0.336007
[224]	valid_0's binary_logloss: 0.335651
[225]	valid_0's binary_logloss: 0.334997
[226]	valid_0's binary_logloss: 0.33483
[227]	valid_0's binary_logloss: 0.334837
[228]	valid_0's binary_logloss: 0.334843
[229]	valid_0's binary_logloss: 0.334845
[230]	valid_0's binary_logloss: 0.334824
[231]	valid_0's binary_logloss: 0.334801
[232]	valid_0's binary_logloss: 0.334173
[233]	valid_0's binary_logloss: 0.334186
[234]	valid_0's binary_logloss: 0.33412
[235]	valid_0's bi

[426]	valid_0's binary_logloss: 0.312769
[427]	valid_0's binary_logloss: 0.312764
[428]	valid_0's binary_logloss: 0.312767
[429]	valid_0's binary_logloss: 0.312763
[430]	valid_0's binary_logloss: 0.312757
[431]	valid_0's binary_logloss: 0.312733
[432]	valid_0's binary_logloss: 0.312722
[433]	valid_0's binary_logloss: 0.312687
[434]	valid_0's binary_logloss: 0.31271
[435]	valid_0's binary_logloss: 0.312719
[436]	valid_0's binary_logloss: 0.312729
[437]	valid_0's binary_logloss: 0.3127
[438]	valid_0's binary_logloss: 0.312722
[439]	valid_0's binary_logloss: 0.312727
[440]	valid_0's binary_logloss: 0.312735
[441]	valid_0's binary_logloss: 0.312753
[442]	valid_0's binary_logloss: 0.31273
[443]	valid_0's binary_logloss: 0.312721
[444]	valid_0's binary_logloss: 0.312719
[445]	valid_0's binary_logloss: 0.312696
[446]	valid_0's binary_logloss: 0.312709
[447]	valid_0's binary_logloss: 0.312702
[448]	valid_0's binary_logloss: 0.312701
[449]	valid_0's binary_logloss: 0.312473
[450]	valid_0's bina

[628]	valid_0's binary_logloss: 0.301375
[629]	valid_0's binary_logloss: 0.301336
[630]	valid_0's binary_logloss: 0.301336
[631]	valid_0's binary_logloss: 0.301309
[632]	valid_0's binary_logloss: 0.301269
[633]	valid_0's binary_logloss: 0.300997
[634]	valid_0's binary_logloss: 0.300946
[635]	valid_0's binary_logloss: 0.300631
[636]	valid_0's binary_logloss: 0.30065
[637]	valid_0's binary_logloss: 0.300621
[638]	valid_0's binary_logloss: 0.300622
[639]	valid_0's binary_logloss: 0.300607
[640]	valid_0's binary_logloss: 0.300617
[641]	valid_0's binary_logloss: 0.30062
[642]	valid_0's binary_logloss: 0.30062
[643]	valid_0's binary_logloss: 0.300574
[644]	valid_0's binary_logloss: 0.300548
[645]	valid_0's binary_logloss: 0.300527
[646]	valid_0's binary_logloss: 0.300366
[647]	valid_0's binary_logloss: 0.300347
[648]	valid_0's binary_logloss: 0.300356
[649]	valid_0's binary_logloss: 0.300342
[650]	valid_0's binary_logloss: 0.300321
[651]	valid_0's binary_logloss: 0.300315
[652]	valid_0's bin

[831]	valid_0's binary_logloss: 0.29313
[832]	valid_0's binary_logloss: 0.293123
[833]	valid_0's binary_logloss: 0.293099
[834]	valid_0's binary_logloss: 0.293027
[835]	valid_0's binary_logloss: 0.292944
[836]	valid_0's binary_logloss: 0.292917
[837]	valid_0's binary_logloss: 0.292892
[838]	valid_0's binary_logloss: 0.292835
[839]	valid_0's binary_logloss: 0.292809
[840]	valid_0's binary_logloss: 0.292843
[841]	valid_0's binary_logloss: 0.292868
[842]	valid_0's binary_logloss: 0.292825
[843]	valid_0's binary_logloss: 0.292842
[844]	valid_0's binary_logloss: 0.292773
[845]	valid_0's binary_logloss: 0.29275
[846]	valid_0's binary_logloss: 0.292742
[847]	valid_0's binary_logloss: 0.292625
[848]	valid_0's binary_logloss: 0.292623
[849]	valid_0's binary_logloss: 0.29262
[850]	valid_0's binary_logloss: 0.292622
[851]	valid_0's binary_logloss: 0.29265
[852]	valid_0's binary_logloss: 0.292432
[853]	valid_0's binary_logloss: 0.292438
[854]	valid_0's binary_logloss: 0.292402
[855]	valid_0's bina

[1051]	valid_0's binary_logloss: 0.286359
[1052]	valid_0's binary_logloss: 0.286346
[1053]	valid_0's binary_logloss: 0.286357
[1054]	valid_0's binary_logloss: 0.286366
[1055]	valid_0's binary_logloss: 0.286341
[1056]	valid_0's binary_logloss: 0.28636
[1057]	valid_0's binary_logloss: 0.286377
[1058]	valid_0's binary_logloss: 0.286318
[1059]	valid_0's binary_logloss: 0.286229
[1060]	valid_0's binary_logloss: 0.286242
[1061]	valid_0's binary_logloss: 0.28623
[1062]	valid_0's binary_logloss: 0.286226
[1063]	valid_0's binary_logloss: 0.286207
[1064]	valid_0's binary_logloss: 0.286224
[1065]	valid_0's binary_logloss: 0.286204
[1066]	valid_0's binary_logloss: 0.286184
[1067]	valid_0's binary_logloss: 0.285977
[1068]	valid_0's binary_logloss: 0.285987
[1069]	valid_0's binary_logloss: 0.285993
[1070]	valid_0's binary_logloss: 0.285895
[1071]	valid_0's binary_logloss: 0.285886
[1072]	valid_0's binary_logloss: 0.285893
[1073]	valid_0's binary_logloss: 0.285883
[1074]	valid_0's binary_logloss: 0.2

[1273]	valid_0's binary_logloss: 0.283602
[1274]	valid_0's binary_logloss: 0.283594
[1275]	valid_0's binary_logloss: 0.283599
[1276]	valid_0's binary_logloss: 0.283601
[1277]	valid_0's binary_logloss: 0.283511
[1278]	valid_0's binary_logloss: 0.283496
[1279]	valid_0's binary_logloss: 0.283496
[1280]	valid_0's binary_logloss: 0.283497
[1281]	valid_0's binary_logloss: 0.28349
[1282]	valid_0's binary_logloss: 0.28329
[1283]	valid_0's binary_logloss: 0.28329
[1284]	valid_0's binary_logloss: 0.283295
[1285]	valid_0's binary_logloss: 0.283139
[1286]	valid_0's binary_logloss: 0.28316
[1287]	valid_0's binary_logloss: 0.283135
[1288]	valid_0's binary_logloss: 0.283124
[1289]	valid_0's binary_logloss: 0.283128
[1290]	valid_0's binary_logloss: 0.283147
[1291]	valid_0's binary_logloss: 0.283146
[1292]	valid_0's binary_logloss: 0.282956
[1293]	valid_0's binary_logloss: 0.28272
[1294]	valid_0's binary_logloss: 0.282695
[1295]	valid_0's binary_logloss: 0.282686
[1296]	valid_0's binary_logloss: 0.2826

[1489]	valid_0's binary_logloss: 0.27968
[1490]	valid_0's binary_logloss: 0.279645
[1491]	valid_0's binary_logloss: 0.279546
[1492]	valid_0's binary_logloss: 0.279539
[1493]	valid_0's binary_logloss: 0.279542
[1494]	valid_0's binary_logloss: 0.279533
[1495]	valid_0's binary_logloss: 0.279527
[1496]	valid_0's binary_logloss: 0.279523
[1497]	valid_0's binary_logloss: 0.279534
[1498]	valid_0's binary_logloss: 0.279531
[1499]	valid_0's binary_logloss: 0.279534
[1500]	valid_0's binary_logloss: 0.279542
[1501]	valid_0's binary_logloss: 0.279565
[1502]	valid_0's binary_logloss: 0.279573
[1503]	valid_0's binary_logloss: 0.279588
[1504]	valid_0's binary_logloss: 0.279588
[1505]	valid_0's binary_logloss: 0.27957
[1506]	valid_0's binary_logloss: 0.279527
[1507]	valid_0's binary_logloss: 0.279552
[1508]	valid_0's binary_logloss: 0.279528
[1509]	valid_0's binary_logloss: 0.279527
[1510]	valid_0's binary_logloss: 0.279518
[1511]	valid_0's binary_logloss: 0.279486
[1512]	valid_0's binary_logloss: 0.2

In [26]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=100,subsample=0.8)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.490695
[2]	valid_0's binary_logloss: 0.480803
[3]	valid_0's binary_logloss: 0.472525
[4]	valid_0's binary_logloss: 0.465707
[5]	valid_0's binary_logloss: 0.459782
[6]	valid_0's binary_logloss: 0.454939
[7]	valid_0's binary_logloss: 0.450484
[8]	valid_0's binary_logloss: 0.446788
[9]	valid_0's binary_logloss: 0.443357
[10]	valid_0's binary_logloss: 0.440521
[11]	valid_0's binary_logloss: 0.437527
[12]	valid_0's binary_logloss: 0.434931
[13]	valid_0's binary_logloss: 0.432874
[14]	valid_0's binary_logloss: 0.430052
[15]	valid_0's binary_logloss: 0.428121
[16]	valid_0's binary_logloss: 0.426233
[17]	valid_0's binary_logloss: 0.424511
[18]	valid_0's binary_logloss: 0.422734
[19]	valid_0's binary_logloss: 0.420994
[20]	valid_0's binary_logloss: 0.419555
[21]	valid_0's binary_logloss: 0.418144
[22]	valid_0's binary_logloss: 0.416744
[23]	valid_0's binary_logloss: 0.415624
[24]	valid_0's binary_logloss: 0.414589
[25]	valid_0's binary_logloss: 0.413439
[26]	vali

[211]	valid_0's binary_logloss: 0.328327
[212]	valid_0's binary_logloss: 0.328264
[213]	valid_0's binary_logloss: 0.328245
[214]	valid_0's binary_logloss: 0.328213
[215]	valid_0's binary_logloss: 0.327999
[216]	valid_0's binary_logloss: 0.328002
[217]	valid_0's binary_logloss: 0.327694
[218]	valid_0's binary_logloss: 0.327676
[219]	valid_0's binary_logloss: 0.327338
[220]	valid_0's binary_logloss: 0.327045
[221]	valid_0's binary_logloss: 0.326999
[222]	valid_0's binary_logloss: 0.327014
[223]	valid_0's binary_logloss: 0.326727
[224]	valid_0's binary_logloss: 0.326581
[225]	valid_0's binary_logloss: 0.325935
[226]	valid_0's binary_logloss: 0.325854
[227]	valid_0's binary_logloss: 0.325674
[228]	valid_0's binary_logloss: 0.325512
[229]	valid_0's binary_logloss: 0.325002
[230]	valid_0's binary_logloss: 0.324782
[231]	valid_0's binary_logloss: 0.324779
[232]	valid_0's binary_logloss: 0.324716
[233]	valid_0's binary_logloss: 0.324613
[234]	valid_0's binary_logloss: 0.324595
[235]	valid_0's 

[415]	valid_0's binary_logloss: 0.30588
[416]	valid_0's binary_logloss: 0.305845
[417]	valid_0's binary_logloss: 0.305467
[418]	valid_0's binary_logloss: 0.305468
[419]	valid_0's binary_logloss: 0.305442
[420]	valid_0's binary_logloss: 0.305429
[421]	valid_0's binary_logloss: 0.305388
[422]	valid_0's binary_logloss: 0.305374
[423]	valid_0's binary_logloss: 0.305342
[424]	valid_0's binary_logloss: 0.305319
[425]	valid_0's binary_logloss: 0.305205
[426]	valid_0's binary_logloss: 0.305198
[427]	valid_0's binary_logloss: 0.305214
[428]	valid_0's binary_logloss: 0.305222
[429]	valid_0's binary_logloss: 0.305222
[430]	valid_0's binary_logloss: 0.30512
[431]	valid_0's binary_logloss: 0.304958
[432]	valid_0's binary_logloss: 0.304951
[433]	valid_0's binary_logloss: 0.304947
[434]	valid_0's binary_logloss: 0.304942
[435]	valid_0's binary_logloss: 0.304907
[436]	valid_0's binary_logloss: 0.30471
[437]	valid_0's binary_logloss: 0.304701
[438]	valid_0's binary_logloss: 0.30468
[439]	valid_0's bina

[621]	valid_0's binary_logloss: 0.295753
[622]	valid_0's binary_logloss: 0.295788
[623]	valid_0's binary_logloss: 0.295416
[624]	valid_0's binary_logloss: 0.295292
[625]	valid_0's binary_logloss: 0.295322
[626]	valid_0's binary_logloss: 0.295321
[627]	valid_0's binary_logloss: 0.295326
[628]	valid_0's binary_logloss: 0.295336
[629]	valid_0's binary_logloss: 0.295333
[630]	valid_0's binary_logloss: 0.295291
[631]	valid_0's binary_logloss: 0.295256
[632]	valid_0's binary_logloss: 0.295271
[633]	valid_0's binary_logloss: 0.295287
[634]	valid_0's binary_logloss: 0.295252
[635]	valid_0's binary_logloss: 0.295222
[636]	valid_0's binary_logloss: 0.295123
[637]	valid_0's binary_logloss: 0.295101
[638]	valid_0's binary_logloss: 0.294887
[639]	valid_0's binary_logloss: 0.29487
[640]	valid_0's binary_logloss: 0.294892
[641]	valid_0's binary_logloss: 0.294559
[642]	valid_0's binary_logloss: 0.294561
[643]	valid_0's binary_logloss: 0.294484
[644]	valid_0's binary_logloss: 0.294452
[645]	valid_0's b

[832]	valid_0's binary_logloss: 0.288139
[833]	valid_0's binary_logloss: 0.288074
[834]	valid_0's binary_logloss: 0.288074
[835]	valid_0's binary_logloss: 0.288072
[836]	valid_0's binary_logloss: 0.288055
[837]	valid_0's binary_logloss: 0.288061
[838]	valid_0's binary_logloss: 0.288065
[839]	valid_0's binary_logloss: 0.287944
[840]	valid_0's binary_logloss: 0.287957
[841]	valid_0's binary_logloss: 0.287959
[842]	valid_0's binary_logloss: 0.287952
[843]	valid_0's binary_logloss: 0.287882
[844]	valid_0's binary_logloss: 0.287768
[845]	valid_0's binary_logloss: 0.28774
[846]	valid_0's binary_logloss: 0.287718
[847]	valid_0's binary_logloss: 0.287686
[848]	valid_0's binary_logloss: 0.287626
[849]	valid_0's binary_logloss: 0.287624
[850]	valid_0's binary_logloss: 0.287646
[851]	valid_0's binary_logloss: 0.287671
[852]	valid_0's binary_logloss: 0.287672
[853]	valid_0's binary_logloss: 0.287676
[854]	valid_0's binary_logloss: 0.287678
[855]	valid_0's binary_logloss: 0.287714
[856]	valid_0's b

[1052]	valid_0's binary_logloss: 0.282059
[1053]	valid_0's binary_logloss: 0.282082
[1054]	valid_0's binary_logloss: 0.282072
[1055]	valid_0's binary_logloss: 0.28204
[1056]	valid_0's binary_logloss: 0.282033
[1057]	valid_0's binary_logloss: 0.282031
[1058]	valid_0's binary_logloss: 0.281947
[1059]	valid_0's binary_logloss: 0.281966
[1060]	valid_0's binary_logloss: 0.281986
[1061]	valid_0's binary_logloss: 0.28197
[1062]	valid_0's binary_logloss: 0.281973
[1063]	valid_0's binary_logloss: 0.281996
[1064]	valid_0's binary_logloss: 0.282001
[1065]	valid_0's binary_logloss: 0.282003
[1066]	valid_0's binary_logloss: 0.281992
[1067]	valid_0's binary_logloss: 0.281997
[1068]	valid_0's binary_logloss: 0.282002
[1069]	valid_0's binary_logloss: 0.282033
[1070]	valid_0's binary_logloss: 0.282059
[1071]	valid_0's binary_logloss: 0.282062
[1072]	valid_0's binary_logloss: 0.282015
[1073]	valid_0's binary_logloss: 0.282038
[1074]	valid_0's binary_logloss: 0.282062
[1075]	valid_0's binary_logloss: 0.2

[1268]	valid_0's binary_logloss: 0.278546
[1269]	valid_0's binary_logloss: 0.278531
[1270]	valid_0's binary_logloss: 0.278435
[1271]	valid_0's binary_logloss: 0.278485
[1272]	valid_0's binary_logloss: 0.278478
[1273]	valid_0's binary_logloss: 0.278483
[1274]	valid_0's binary_logloss: 0.278529
[1275]	valid_0's binary_logloss: 0.278555
[1276]	valid_0's binary_logloss: 0.278571
[1277]	valid_0's binary_logloss: 0.278569
[1278]	valid_0's binary_logloss: 0.278594
[1279]	valid_0's binary_logloss: 0.278603
[1280]	valid_0's binary_logloss: 0.278577
[1281]	valid_0's binary_logloss: 0.278591
[1282]	valid_0's binary_logloss: 0.278596
[1283]	valid_0's binary_logloss: 0.278639
[1284]	valid_0's binary_logloss: 0.278645
[1285]	valid_0's binary_logloss: 0.278649
[1286]	valid_0's binary_logloss: 0.278664
[1287]	valid_0's binary_logloss: 0.278682
[1288]	valid_0's binary_logloss: 0.278662
[1289]	valid_0's binary_logloss: 0.27857
[1290]	valid_0's binary_logloss: 0.278551
[1291]	valid_0's binary_logloss: 0.

[1467]	valid_0's binary_logloss: 0.276801
[1468]	valid_0's binary_logloss: 0.276843
[1469]	valid_0's binary_logloss: 0.276855
[1470]	valid_0's binary_logloss: 0.276787
[1471]	valid_0's binary_logloss: 0.276719
[1472]	valid_0's binary_logloss: 0.276755
[1473]	valid_0's binary_logloss: 0.276771
[1474]	valid_0's binary_logloss: 0.276778
[1475]	valid_0's binary_logloss: 0.276802
[1476]	valid_0's binary_logloss: 0.276819
[1477]	valid_0's binary_logloss: 0.276851
[1478]	valid_0's binary_logloss: 0.276716
[1479]	valid_0's binary_logloss: 0.276706
[1480]	valid_0's binary_logloss: 0.276719
[1481]	valid_0's binary_logloss: 0.276745
[1482]	valid_0's binary_logloss: 0.27678
[1483]	valid_0's binary_logloss: 0.276778
[1484]	valid_0's binary_logloss: 0.276784
[1485]	valid_0's binary_logloss: 0.276813
[1486]	valid_0's binary_logloss: 0.276825
[1487]	valid_0's binary_logloss: 0.27684
[1488]	valid_0's binary_logloss: 0.276869
[1489]	valid_0's binary_logloss: 0.276897
[1490]	valid_0's binary_logloss: 0.2

In [27]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=100,subsample=0.7)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.490695
[2]	valid_0's binary_logloss: 0.480803
[3]	valid_0's binary_logloss: 0.472525
[4]	valid_0's binary_logloss: 0.465707
[5]	valid_0's binary_logloss: 0.459782
[6]	valid_0's binary_logloss: 0.454939
[7]	valid_0's binary_logloss: 0.450484
[8]	valid_0's binary_logloss: 0.446788
[9]	valid_0's binary_logloss: 0.443357
[10]	valid_0's binary_logloss: 0.440521
[11]	valid_0's binary_logloss: 0.437527
[12]	valid_0's binary_logloss: 0.434931
[13]	valid_0's binary_logloss: 0.432874
[14]	valid_0's binary_logloss: 0.430052
[15]	valid_0's binary_logloss: 0.428121
[16]	valid_0's binary_logloss: 0.426233
[17]	valid_0's binary_logloss: 0.424511
[18]	valid_0's binary_logloss: 0.422734
[19]	valid_0's binary_logloss: 0.420994
[20]	valid_0's binary_logloss: 0.419555
[21]	valid_0's binary_logloss: 0.418144
[22]	valid_0's binary_logloss: 0.416744
[23]	valid_0's binary_logloss: 0.415624
[24]	valid_0's binary_logloss: 0.414589
[25]	valid_0's binary_logloss: 0.413439
[26]	vali

[205]	valid_0's binary_logloss: 0.329514
[206]	valid_0's binary_logloss: 0.329101
[207]	valid_0's binary_logloss: 0.329042
[208]	valid_0's binary_logloss: 0.329004
[209]	valid_0's binary_logloss: 0.328649
[210]	valid_0's binary_logloss: 0.328325
[211]	valid_0's binary_logloss: 0.328327
[212]	valid_0's binary_logloss: 0.328264
[213]	valid_0's binary_logloss: 0.328245
[214]	valid_0's binary_logloss: 0.328213
[215]	valid_0's binary_logloss: 0.327999
[216]	valid_0's binary_logloss: 0.328002
[217]	valid_0's binary_logloss: 0.327694
[218]	valid_0's binary_logloss: 0.327676
[219]	valid_0's binary_logloss: 0.327338
[220]	valid_0's binary_logloss: 0.327045
[221]	valid_0's binary_logloss: 0.326999
[222]	valid_0's binary_logloss: 0.327014
[223]	valid_0's binary_logloss: 0.326727
[224]	valid_0's binary_logloss: 0.326581
[225]	valid_0's binary_logloss: 0.325935
[226]	valid_0's binary_logloss: 0.325854
[227]	valid_0's binary_logloss: 0.325674
[228]	valid_0's binary_logloss: 0.325512
[229]	valid_0's 

[417]	valid_0's binary_logloss: 0.305467
[418]	valid_0's binary_logloss: 0.305468
[419]	valid_0's binary_logloss: 0.305442
[420]	valid_0's binary_logloss: 0.305429
[421]	valid_0's binary_logloss: 0.305388
[422]	valid_0's binary_logloss: 0.305374
[423]	valid_0's binary_logloss: 0.305342
[424]	valid_0's binary_logloss: 0.305319
[425]	valid_0's binary_logloss: 0.305205
[426]	valid_0's binary_logloss: 0.305198
[427]	valid_0's binary_logloss: 0.305214
[428]	valid_0's binary_logloss: 0.305222
[429]	valid_0's binary_logloss: 0.305222
[430]	valid_0's binary_logloss: 0.30512
[431]	valid_0's binary_logloss: 0.304958
[432]	valid_0's binary_logloss: 0.304951
[433]	valid_0's binary_logloss: 0.304947
[434]	valid_0's binary_logloss: 0.304942
[435]	valid_0's binary_logloss: 0.304907
[436]	valid_0's binary_logloss: 0.30471
[437]	valid_0's binary_logloss: 0.304701
[438]	valid_0's binary_logloss: 0.30468
[439]	valid_0's binary_logloss: 0.304705
[440]	valid_0's binary_logloss: 0.304641
[441]	valid_0's bin

[626]	valid_0's binary_logloss: 0.295321
[627]	valid_0's binary_logloss: 0.295326
[628]	valid_0's binary_logloss: 0.295336
[629]	valid_0's binary_logloss: 0.295333
[630]	valid_0's binary_logloss: 0.295291
[631]	valid_0's binary_logloss: 0.295256
[632]	valid_0's binary_logloss: 0.295271
[633]	valid_0's binary_logloss: 0.295287
[634]	valid_0's binary_logloss: 0.295252
[635]	valid_0's binary_logloss: 0.295222
[636]	valid_0's binary_logloss: 0.295123
[637]	valid_0's binary_logloss: 0.295101
[638]	valid_0's binary_logloss: 0.294887
[639]	valid_0's binary_logloss: 0.29487
[640]	valid_0's binary_logloss: 0.294892
[641]	valid_0's binary_logloss: 0.294559
[642]	valid_0's binary_logloss: 0.294561
[643]	valid_0's binary_logloss: 0.294484
[644]	valid_0's binary_logloss: 0.294452
[645]	valid_0's binary_logloss: 0.294478
[646]	valid_0's binary_logloss: 0.294255
[647]	valid_0's binary_logloss: 0.294236
[648]	valid_0's binary_logloss: 0.29422
[649]	valid_0's binary_logloss: 0.294226
[650]	valid_0's bi

[837]	valid_0's binary_logloss: 0.288061
[838]	valid_0's binary_logloss: 0.288065
[839]	valid_0's binary_logloss: 0.287944
[840]	valid_0's binary_logloss: 0.287957
[841]	valid_0's binary_logloss: 0.287959
[842]	valid_0's binary_logloss: 0.287952
[843]	valid_0's binary_logloss: 0.287882
[844]	valid_0's binary_logloss: 0.287768
[845]	valid_0's binary_logloss: 0.28774
[846]	valid_0's binary_logloss: 0.287718
[847]	valid_0's binary_logloss: 0.287686
[848]	valid_0's binary_logloss: 0.287626
[849]	valid_0's binary_logloss: 0.287624
[850]	valid_0's binary_logloss: 0.287646
[851]	valid_0's binary_logloss: 0.287671
[852]	valid_0's binary_logloss: 0.287672
[853]	valid_0's binary_logloss: 0.287676
[854]	valid_0's binary_logloss: 0.287678
[855]	valid_0's binary_logloss: 0.287714
[856]	valid_0's binary_logloss: 0.287719
[857]	valid_0's binary_logloss: 0.287509
[858]	valid_0's binary_logloss: 0.287365
[859]	valid_0's binary_logloss: 0.287365
[860]	valid_0's binary_logloss: 0.287387
[861]	valid_0's b

[1048]	valid_0's binary_logloss: 0.282016
[1049]	valid_0's binary_logloss: 0.282007
[1050]	valid_0's binary_logloss: 0.282023
[1051]	valid_0's binary_logloss: 0.28205
[1052]	valid_0's binary_logloss: 0.282059
[1053]	valid_0's binary_logloss: 0.282082
[1054]	valid_0's binary_logloss: 0.282072
[1055]	valid_0's binary_logloss: 0.28204
[1056]	valid_0's binary_logloss: 0.282033
[1057]	valid_0's binary_logloss: 0.282031
[1058]	valid_0's binary_logloss: 0.281947
[1059]	valid_0's binary_logloss: 0.281966
[1060]	valid_0's binary_logloss: 0.281986
[1061]	valid_0's binary_logloss: 0.28197
[1062]	valid_0's binary_logloss: 0.281973
[1063]	valid_0's binary_logloss: 0.281996
[1064]	valid_0's binary_logloss: 0.282001
[1065]	valid_0's binary_logloss: 0.282003
[1066]	valid_0's binary_logloss: 0.281992
[1067]	valid_0's binary_logloss: 0.281997
[1068]	valid_0's binary_logloss: 0.282002
[1069]	valid_0's binary_logloss: 0.282033
[1070]	valid_0's binary_logloss: 0.282059
[1071]	valid_0's binary_logloss: 0.28

[1258]	valid_0's binary_logloss: 0.278703
[1259]	valid_0's binary_logloss: 0.278601
[1260]	valid_0's binary_logloss: 0.278613
[1261]	valid_0's binary_logloss: 0.278603
[1262]	valid_0's binary_logloss: 0.278557
[1263]	valid_0's binary_logloss: 0.278542
[1264]	valid_0's binary_logloss: 0.278556
[1265]	valid_0's binary_logloss: 0.278515
[1266]	valid_0's binary_logloss: 0.278537
[1267]	valid_0's binary_logloss: 0.278535
[1268]	valid_0's binary_logloss: 0.278546
[1269]	valid_0's binary_logloss: 0.278531
[1270]	valid_0's binary_logloss: 0.278435
[1271]	valid_0's binary_logloss: 0.278485
[1272]	valid_0's binary_logloss: 0.278478
[1273]	valid_0's binary_logloss: 0.278483
[1274]	valid_0's binary_logloss: 0.278529
[1275]	valid_0's binary_logloss: 0.278555
[1276]	valid_0's binary_logloss: 0.278571
[1277]	valid_0's binary_logloss: 0.278569
[1278]	valid_0's binary_logloss: 0.278594
[1279]	valid_0's binary_logloss: 0.278603
[1280]	valid_0's binary_logloss: 0.278577
[1281]	valid_0's binary_logloss: 0

[1460]	valid_0's binary_logloss: 0.276793
[1461]	valid_0's binary_logloss: 0.276785
[1462]	valid_0's binary_logloss: 0.276764
[1463]	valid_0's binary_logloss: 0.276788
[1464]	valid_0's binary_logloss: 0.276783
[1465]	valid_0's binary_logloss: 0.27678
[1466]	valid_0's binary_logloss: 0.276775
[1467]	valid_0's binary_logloss: 0.276801
[1468]	valid_0's binary_logloss: 0.276843
[1469]	valid_0's binary_logloss: 0.276855
[1470]	valid_0's binary_logloss: 0.276787
[1471]	valid_0's binary_logloss: 0.276719
[1472]	valid_0's binary_logloss: 0.276755
[1473]	valid_0's binary_logloss: 0.276771
[1474]	valid_0's binary_logloss: 0.276778
[1475]	valid_0's binary_logloss: 0.276802
[1476]	valid_0's binary_logloss: 0.276819
[1477]	valid_0's binary_logloss: 0.276851
[1478]	valid_0's binary_logloss: 0.276716
[1479]	valid_0's binary_logloss: 0.276706
[1480]	valid_0's binary_logloss: 0.276719
[1481]	valid_0's binary_logloss: 0.276745
[1482]	valid_0's binary_logloss: 0.27678
[1483]	valid_0's binary_logloss: 0.2

In [10]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=80,subsample=0.7)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491029
[2]	valid_0's binary_logloss: 0.481423
[3]	valid_0's binary_logloss: 0.473585
[4]	valid_0's binary_logloss: 0.467049
[5]	valid_0's binary_logloss: 0.461671
[6]	valid_0's binary_logloss: 0.456964
[7]	valid_0's binary_logloss: 0.452862
[8]	valid_0's binary_logloss: 0.449481
[9]	valid_0's binary_logloss: 0.446126
[10]	valid_0's binary_logloss: 0.443096
[11]	valid_0's binary_logloss: 0.440703
[12]	valid_0's binary_logloss: 0.438571
[13]	valid_0's binary_logloss: 0.436462
[14]	valid_0's binary_logloss: 0.434473
[15]	valid_0's binary_logloss: 0.432062
[16]	valid_0's binary_logloss: 0.430186
[17]	valid_0's binary_logloss: 0.42804
[18]	valid_0's binary_logloss: 0.426584
[19]	valid_0's binary_logloss: 0.42486
[20]	valid_0's binary_logloss: 0.423681
[21]	valid_0's binary_logloss: 0.422409
[22]	valid_0's binary_logloss: 0.420936
[23]	valid_0's binary_logloss: 0.419946
[24]	valid_0's binary_logloss: 0.418639
[25]	valid_0's binary_logloss: 0.417779
[26]	valid_

[218]	valid_0's binary_logloss: 0.336639
[219]	valid_0's binary_logloss: 0.336595
[220]	valid_0's binary_logloss: 0.336559
[221]	valid_0's binary_logloss: 0.336514
[222]	valid_0's binary_logloss: 0.336504
[223]	valid_0's binary_logloss: 0.336007
[224]	valid_0's binary_logloss: 0.335651
[225]	valid_0's binary_logloss: 0.334997
[226]	valid_0's binary_logloss: 0.33483
[227]	valid_0's binary_logloss: 0.334837
[228]	valid_0's binary_logloss: 0.334843
[229]	valid_0's binary_logloss: 0.334845
[230]	valid_0's binary_logloss: 0.334824
[231]	valid_0's binary_logloss: 0.334801
[232]	valid_0's binary_logloss: 0.334173
[233]	valid_0's binary_logloss: 0.334186
[234]	valid_0's binary_logloss: 0.33412
[235]	valid_0's binary_logloss: 0.334079
[236]	valid_0's binary_logloss: 0.334023
[237]	valid_0's binary_logloss: 0.333978
[238]	valid_0's binary_logloss: 0.333575
[239]	valid_0's binary_logloss: 0.333567
[240]	valid_0's binary_logloss: 0.333524
[241]	valid_0's binary_logloss: 0.333544
[242]	valid_0's bi

[428]	valid_0's binary_logloss: 0.312767
[429]	valid_0's binary_logloss: 0.312763
[430]	valid_0's binary_logloss: 0.312757
[431]	valid_0's binary_logloss: 0.312733
[432]	valid_0's binary_logloss: 0.312722
[433]	valid_0's binary_logloss: 0.312687
[434]	valid_0's binary_logloss: 0.31271
[435]	valid_0's binary_logloss: 0.312719
[436]	valid_0's binary_logloss: 0.312729
[437]	valid_0's binary_logloss: 0.3127
[438]	valid_0's binary_logloss: 0.312722
[439]	valid_0's binary_logloss: 0.312727
[440]	valid_0's binary_logloss: 0.312735
[441]	valid_0's binary_logloss: 0.312753
[442]	valid_0's binary_logloss: 0.31273
[443]	valid_0's binary_logloss: 0.312721
[444]	valid_0's binary_logloss: 0.312719
[445]	valid_0's binary_logloss: 0.312696
[446]	valid_0's binary_logloss: 0.312709
[447]	valid_0's binary_logloss: 0.312702
[448]	valid_0's binary_logloss: 0.312701
[449]	valid_0's binary_logloss: 0.312473
[450]	valid_0's binary_logloss: 0.312146
[451]	valid_0's binary_logloss: 0.312111
[452]	valid_0's bina

[650]	valid_0's binary_logloss: 0.300321
[651]	valid_0's binary_logloss: 0.300315
[652]	valid_0's binary_logloss: 0.30032
[653]	valid_0's binary_logloss: 0.300334
[654]	valid_0's binary_logloss: 0.300347
[655]	valid_0's binary_logloss: 0.300331
[656]	valid_0's binary_logloss: 0.300328
[657]	valid_0's binary_logloss: 0.300307
[658]	valid_0's binary_logloss: 0.300305
[659]	valid_0's binary_logloss: 0.300318
[660]	valid_0's binary_logloss: 0.300349
[661]	valid_0's binary_logloss: 0.300319
[662]	valid_0's binary_logloss: 0.300317
[663]	valid_0's binary_logloss: 0.300316
[664]	valid_0's binary_logloss: 0.300135
[665]	valid_0's binary_logloss: 0.300118
[666]	valid_0's binary_logloss: 0.300104
[667]	valid_0's binary_logloss: 0.300117
[668]	valid_0's binary_logloss: 0.300124
[669]	valid_0's binary_logloss: 0.300132
[670]	valid_0's binary_logloss: 0.30008
[671]	valid_0's binary_logloss: 0.300084
[672]	valid_0's binary_logloss: 0.30005
[673]	valid_0's binary_logloss: 0.3
[674]	valid_0's binary_l

[856]	valid_0's binary_logloss: 0.292389
[857]	valid_0's binary_logloss: 0.292392
[858]	valid_0's binary_logloss: 0.292297
[859]	valid_0's binary_logloss: 0.292235
[860]	valid_0's binary_logloss: 0.292228
[861]	valid_0's binary_logloss: 0.292248
[862]	valid_0's binary_logloss: 0.292219
[863]	valid_0's binary_logloss: 0.291949
[864]	valid_0's binary_logloss: 0.291935
[865]	valid_0's binary_logloss: 0.291943
[866]	valid_0's binary_logloss: 0.291926
[867]	valid_0's binary_logloss: 0.291939
[868]	valid_0's binary_logloss: 0.291936
[869]	valid_0's binary_logloss: 0.291898
[870]	valid_0's binary_logloss: 0.291932
[871]	valid_0's binary_logloss: 0.291925
[872]	valid_0's binary_logloss: 0.291948
[873]	valid_0's binary_logloss: 0.291943
[874]	valid_0's binary_logloss: 0.291787
[875]	valid_0's binary_logloss: 0.291704
[876]	valid_0's binary_logloss: 0.291658
[877]	valid_0's binary_logloss: 0.291646
[878]	valid_0's binary_logloss: 0.291659
[879]	valid_0's binary_logloss: 0.291698
[880]	valid_0's 

[1055]	valid_0's binary_logloss: 0.286341
[1056]	valid_0's binary_logloss: 0.28636
[1057]	valid_0's binary_logloss: 0.286377
[1058]	valid_0's binary_logloss: 0.286318
[1059]	valid_0's binary_logloss: 0.286229
[1060]	valid_0's binary_logloss: 0.286242
[1061]	valid_0's binary_logloss: 0.28623
[1062]	valid_0's binary_logloss: 0.286226
[1063]	valid_0's binary_logloss: 0.286207
[1064]	valid_0's binary_logloss: 0.286224
[1065]	valid_0's binary_logloss: 0.286204
[1066]	valid_0's binary_logloss: 0.286184
[1067]	valid_0's binary_logloss: 0.285977
[1068]	valid_0's binary_logloss: 0.285987
[1069]	valid_0's binary_logloss: 0.285993
[1070]	valid_0's binary_logloss: 0.285895
[1071]	valid_0's binary_logloss: 0.285886
[1072]	valid_0's binary_logloss: 0.285893
[1073]	valid_0's binary_logloss: 0.285883
[1074]	valid_0's binary_logloss: 0.285867
[1075]	valid_0's binary_logloss: 0.285877
[1076]	valid_0's binary_logloss: 0.285893
[1077]	valid_0's binary_logloss: 0.285899
[1078]	valid_0's binary_logloss: 0.2

[1261]	valid_0's binary_logloss: 0.283716
[1262]	valid_0's binary_logloss: 0.283741
[1263]	valid_0's binary_logloss: 0.283732
[1264]	valid_0's binary_logloss: 0.28367
[1265]	valid_0's binary_logloss: 0.283675
[1266]	valid_0's binary_logloss: 0.283592
[1267]	valid_0's binary_logloss: 0.283583
[1268]	valid_0's binary_logloss: 0.283558
[1269]	valid_0's binary_logloss: 0.283576
[1270]	valid_0's binary_logloss: 0.283594
[1271]	valid_0's binary_logloss: 0.283611
[1272]	valid_0's binary_logloss: 0.283602
[1273]	valid_0's binary_logloss: 0.283602
[1274]	valid_0's binary_logloss: 0.283594
[1275]	valid_0's binary_logloss: 0.283599
[1276]	valid_0's binary_logloss: 0.283601
[1277]	valid_0's binary_logloss: 0.283511
[1278]	valid_0's binary_logloss: 0.283496
[1279]	valid_0's binary_logloss: 0.283496
[1280]	valid_0's binary_logloss: 0.283497
[1281]	valid_0's binary_logloss: 0.28349
[1282]	valid_0's binary_logloss: 0.28329
[1283]	valid_0's binary_logloss: 0.28329
[1284]	valid_0's binary_logloss: 0.283

[1463]	valid_0's binary_logloss: 0.280517
[1464]	valid_0's binary_logloss: 0.280459
[1465]	valid_0's binary_logloss: 0.28045
[1466]	valid_0's binary_logloss: 0.280468
[1467]	valid_0's binary_logloss: 0.280488
[1468]	valid_0's binary_logloss: 0.280516
[1469]	valid_0's binary_logloss: 0.280264
[1470]	valid_0's binary_logloss: 0.280085
[1471]	valid_0's binary_logloss: 0.279953
[1472]	valid_0's binary_logloss: 0.279968
[1473]	valid_0's binary_logloss: 0.27997
[1474]	valid_0's binary_logloss: 0.279961
[1475]	valid_0's binary_logloss: 0.279897
[1476]	valid_0's binary_logloss: 0.279858
[1477]	valid_0's binary_logloss: 0.279736
[1478]	valid_0's binary_logloss: 0.279714
[1479]	valid_0's binary_logloss: 0.279718
[1480]	valid_0's binary_logloss: 0.279728
[1481]	valid_0's binary_logloss: 0.27975
[1482]	valid_0's binary_logloss: 0.279765
[1483]	valid_0's binary_logloss: 0.279752
[1484]	valid_0's binary_logloss: 0.279758
[1485]	valid_0's binary_logloss: 0.279722
[1486]	valid_0's binary_logloss: 0.27

In [11]:
lgbm_wrapper = LGBMClassifier(n_estimators=1600,max_depth=128,min_child_samples=60,num_leaves=80,subsample=0.6)

# LightGBM도 XGBoost와 동일하게 조기 중단 수행 가능. 
evals=[(X_val,y_val)]
lgbm_wrapper.fit(X_train, y_train, early_stopping_rounds=100, eval_metric="logloss", 
                 eval_set=evals, verbose=True)
preds = lgbm_wrapper.predict(X_test)
pred_proba = lgbm_wrapper.predict_proba(X_test)[:, 1]
get_clf_eval(y_test, preds, pred_proba)

C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\maini\anaconda3\lib\site-packages\lightgbm\sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[1]	valid_0's binary_logloss: 0.491029
[2]	valid_0's binary_logloss: 0.481423
[3]	valid_0's binary_logloss: 0.473585
[4]	valid_0's binary_logloss: 0.467049
[5]	valid_0's binary_logloss: 0.461671
[6]	valid_0's binary_logloss: 0.456964
[7]	valid_0's binary_logloss: 0.452862
[8]	valid_0's binary_logloss: 0.449481
[9]	valid_0's binary_logloss: 0.446126
[10]	valid_0's binary_logloss: 0.443096
[11]	valid_0's binary_logloss: 0.440703
[12]	valid_0's binary_logloss: 0.438571
[13]	valid_0's binary_logloss: 0.436462
[14]	valid_0's binary_logloss: 0.434473
[15]	valid_0's binary_logloss: 0.432062
[16]	valid_0's binary_logloss: 0.430186
[17]	valid_0's binary_logloss: 0.42804
[18]	valid_0's binary_logloss: 0.426584
[19]	valid_0's binary_logloss: 0.42486
[20]	valid_0's binary_logloss: 0.423681
[21]	valid_0's binary_logloss: 0.422409
[22]	valid_0's binary_logloss: 0.420936
[23]	valid_0's binary_logloss: 0.419946
[24]	valid_0's binary_logloss: 0.418639
[25]	valid_0's binary_logloss: 0.417779
[26]	valid_

[207]	valid_0's binary_logloss: 0.338075
[208]	valid_0's binary_logloss: 0.337931
[209]	valid_0's binary_logloss: 0.337521
[210]	valid_0's binary_logloss: 0.337473
[211]	valid_0's binary_logloss: 0.337463
[212]	valid_0's binary_logloss: 0.337284
[213]	valid_0's binary_logloss: 0.336916
[214]	valid_0's binary_logloss: 0.336852
[215]	valid_0's binary_logloss: 0.336731
[216]	valid_0's binary_logloss: 0.336693
[217]	valid_0's binary_logloss: 0.336616
[218]	valid_0's binary_logloss: 0.336639
[219]	valid_0's binary_logloss: 0.336595
[220]	valid_0's binary_logloss: 0.336559
[221]	valid_0's binary_logloss: 0.336514
[222]	valid_0's binary_logloss: 0.336504
[223]	valid_0's binary_logloss: 0.336007
[224]	valid_0's binary_logloss: 0.335651
[225]	valid_0's binary_logloss: 0.334997
[226]	valid_0's binary_logloss: 0.33483
[227]	valid_0's binary_logloss: 0.334837
[228]	valid_0's binary_logloss: 0.334843
[229]	valid_0's binary_logloss: 0.334845
[230]	valid_0's binary_logloss: 0.334824
[231]	valid_0's b

[621]	valid_0's binary_logloss: 0.301601
[622]	valid_0's binary_logloss: 0.301607
[623]	valid_0's binary_logloss: 0.301581
[624]	valid_0's binary_logloss: 0.301607
[625]	valid_0's binary_logloss: 0.301635
[626]	valid_0's binary_logloss: 0.301525
[627]	valid_0's binary_logloss: 0.301372
[628]	valid_0's binary_logloss: 0.301375
[629]	valid_0's binary_logloss: 0.301336
[630]	valid_0's binary_logloss: 0.301336
[631]	valid_0's binary_logloss: 0.301309
[632]	valid_0's binary_logloss: 0.301269
[633]	valid_0's binary_logloss: 0.300997
[634]	valid_0's binary_logloss: 0.300946
[635]	valid_0's binary_logloss: 0.300631
[636]	valid_0's binary_logloss: 0.30065
[637]	valid_0's binary_logloss: 0.300621
[638]	valid_0's binary_logloss: 0.300622
[639]	valid_0's binary_logloss: 0.300607
[640]	valid_0's binary_logloss: 0.300617
[641]	valid_0's binary_logloss: 0.30062
[642]	valid_0's binary_logloss: 0.30062
[643]	valid_0's binary_logloss: 0.300574
[644]	valid_0's binary_logloss: 0.300548
[645]	valid_0's bin

[840]	valid_0's binary_logloss: 0.292843
[841]	valid_0's binary_logloss: 0.292868
[842]	valid_0's binary_logloss: 0.292825
[843]	valid_0's binary_logloss: 0.292842
[844]	valid_0's binary_logloss: 0.292773
[845]	valid_0's binary_logloss: 0.29275
[846]	valid_0's binary_logloss: 0.292742
[847]	valid_0's binary_logloss: 0.292625
[848]	valid_0's binary_logloss: 0.292623
[849]	valid_0's binary_logloss: 0.29262
[850]	valid_0's binary_logloss: 0.292622
[851]	valid_0's binary_logloss: 0.29265
[852]	valid_0's binary_logloss: 0.292432
[853]	valid_0's binary_logloss: 0.292438
[854]	valid_0's binary_logloss: 0.292402
[855]	valid_0's binary_logloss: 0.292384
[856]	valid_0's binary_logloss: 0.292389
[857]	valid_0's binary_logloss: 0.292392
[858]	valid_0's binary_logloss: 0.292297
[859]	valid_0's binary_logloss: 0.292235
[860]	valid_0's binary_logloss: 0.292228
[861]	valid_0's binary_logloss: 0.292248
[862]	valid_0's binary_logloss: 0.292219
[863]	valid_0's binary_logloss: 0.291949
[864]	valid_0's bin

[1054]	valid_0's binary_logloss: 0.286366
[1055]	valid_0's binary_logloss: 0.286341
[1056]	valid_0's binary_logloss: 0.28636
[1057]	valid_0's binary_logloss: 0.286377
[1058]	valid_0's binary_logloss: 0.286318
[1059]	valid_0's binary_logloss: 0.286229
[1060]	valid_0's binary_logloss: 0.286242
[1061]	valid_0's binary_logloss: 0.28623
[1062]	valid_0's binary_logloss: 0.286226
[1063]	valid_0's binary_logloss: 0.286207
[1064]	valid_0's binary_logloss: 0.286224
[1065]	valid_0's binary_logloss: 0.286204
[1066]	valid_0's binary_logloss: 0.286184
[1067]	valid_0's binary_logloss: 0.285977
[1068]	valid_0's binary_logloss: 0.285987
[1069]	valid_0's binary_logloss: 0.285993
[1070]	valid_0's binary_logloss: 0.285895
[1071]	valid_0's binary_logloss: 0.285886
[1072]	valid_0's binary_logloss: 0.285893
[1073]	valid_0's binary_logloss: 0.285883
[1074]	valid_0's binary_logloss: 0.285867
[1075]	valid_0's binary_logloss: 0.285877
[1076]	valid_0's binary_logloss: 0.285893
[1077]	valid_0's binary_logloss: 0.2

[1276]	valid_0's binary_logloss: 0.283601
[1277]	valid_0's binary_logloss: 0.283511
[1278]	valid_0's binary_logloss: 0.283496
[1279]	valid_0's binary_logloss: 0.283496
[1280]	valid_0's binary_logloss: 0.283497
[1281]	valid_0's binary_logloss: 0.28349
[1282]	valid_0's binary_logloss: 0.28329
[1283]	valid_0's binary_logloss: 0.28329
[1284]	valid_0's binary_logloss: 0.283295
[1285]	valid_0's binary_logloss: 0.283139
[1286]	valid_0's binary_logloss: 0.28316
[1287]	valid_0's binary_logloss: 0.283135
[1288]	valid_0's binary_logloss: 0.283124
[1289]	valid_0's binary_logloss: 0.283128
[1290]	valid_0's binary_logloss: 0.283147
[1291]	valid_0's binary_logloss: 0.283146
[1292]	valid_0's binary_logloss: 0.282956
[1293]	valid_0's binary_logloss: 0.28272
[1294]	valid_0's binary_logloss: 0.282695
[1295]	valid_0's binary_logloss: 0.282686
[1296]	valid_0's binary_logloss: 0.282688
[1297]	valid_0's binary_logloss: 0.28269
[1298]	valid_0's binary_logloss: 0.282679
[1299]	valid_0's binary_logloss: 0.28270

[1486]	valid_0's binary_logloss: 0.279711
[1487]	valid_0's binary_logloss: 0.27973
[1488]	valid_0's binary_logloss: 0.279744
[1489]	valid_0's binary_logloss: 0.27968
[1490]	valid_0's binary_logloss: 0.279645
[1491]	valid_0's binary_logloss: 0.279546
[1492]	valid_0's binary_logloss: 0.279539
[1493]	valid_0's binary_logloss: 0.279542
[1494]	valid_0's binary_logloss: 0.279533
[1495]	valid_0's binary_logloss: 0.279527
[1496]	valid_0's binary_logloss: 0.279523
[1497]	valid_0's binary_logloss: 0.279534
[1498]	valid_0's binary_logloss: 0.279531
[1499]	valid_0's binary_logloss: 0.279534
[1500]	valid_0's binary_logloss: 0.279542
[1501]	valid_0's binary_logloss: 0.279565
[1502]	valid_0's binary_logloss: 0.279573
[1503]	valid_0's binary_logloss: 0.279588
[1504]	valid_0's binary_logloss: 0.279588
[1505]	valid_0's binary_logloss: 0.27957
[1506]	valid_0's binary_logloss: 0.279527
[1507]	valid_0's binary_logloss: 0.279552
[1508]	valid_0's binary_logloss: 0.279528
[1509]	valid_0's binary_logloss: 0.27